In [15]:
# 左眼或右眼图片提取不做任何处理，二分类
import os
import pandas as pd
import shutil
import random
from sklearn.model_selection import train_test_split
from PIL import Image
import numpy as np

def create_directory_structure(base_dir):
    """创建所需的目录结构"""
    # 定义目录结构
    directories = [
        'train/class_depression',
        'train/class_non_depression',
        'val/class_depression',
        'val/class_non_depression',
        'test/class_depression',
        'test/class_non_depression'
    ]
    
    # 创建目录
    for dir_path in directories:
        full_path = os.path.join(base_dir, dir_path)
        os.makedirs(full_path, exist_ok=True)
        print(f"创建目录: {full_path}")

def get_subject_id_from_filename(filename):
    """从文件名中提取对象编号"""
    # 文件名格式如 "1000108__21011_0_0.jpg" 或 "1000108_21013_0_0.jpg"
    # 提取最前面的对象编号
    if '__' in filename:
        return filename.split('__')[0]
    else:
        return filename.split('_')[0]

def is_depressed(row):
    """判断对象是否有抑郁症状"""
    # 根据提供的信息，new_totdepress为1表示有基线抑郁
    # 或者baseline_depression或incident_depression为"是"
    if (row['new_totdepress'] == 1 or 
        row['baseline_depression'] == '是' or 
        row['incident_depression'] == '是'):
        return True
    return False

def split_data(subject_ids, train_ratio=0.7, val_ratio=0.15, test_ratio=0.15):
    """将数据分割为训练集、验证集和测试集"""
    # 先分割训练集和临时集
    train_ids, temp_ids = train_test_split(subject_ids, test_size=1-train_ratio, random_state=42)
    
    # 计算验证集在临时集中的比例
    val_proportion = val_ratio / (val_ratio + test_ratio)
    
    # 分割验证集和测试集
    val_ids, test_ids = train_test_split(temp_ids, test_size=1-val_proportion, random_state=42)
    
    return train_ids, val_ids, test_ids

def preprocess_image(image_path, target_size=(224, 224)):
    """
    预处理视网膜图像以适应RetFound模型
    - 调整大小为目标尺寸
    - 保持纵横比的情况下进行中心裁剪
    - 转换为RGB格式（确保3通道）
    """
    try:
        # 打开图像
        with Image.open(image_path) as img:
            # 转换为RGB格式（处理灰度图或RGBA图）
            if img.mode != 'RGB':
                img = img.convert('RGB')
            
            # 保持纵横比调整大小（先将短边调整到目标尺寸）
            width, height = img.size
            target_width, target_height = target_size
            
            # 计算缩放比例
            ratio = min(target_width / width, target_height / height)
            new_width = int(width * ratio)
            new_height = int(height * ratio)
            
            # 调整大小
            img = img.resize((new_width, new_height), Image.LANCZOS)
            
            # 中心裁剪到目标尺寸
            left = (new_width - target_width) // 2
            top = (new_height - target_height) // 2
            right = left + target_width
            bottom = top + target_height
            
            img = img.crop((left, top, right, bottom))
            
            return img
    except Exception as e:
        print(f"预处理图像 {image_path} 时出错: {str(e)}")
        return None

def process_images(left_dir, right_dir, eye_type, excel_path, output_dir, target_size=(224, 224)):
    """处理图像并按照抑郁状态和数据集类型分类，包含预处理步骤"""
    # 读取Excel文件
    df = pd.read_excel(excel_path)
    print(f"成功读取Excel文件，共 {len(df)} 条记录")
    
    # 创建目录结构
    create_directory_structure(output_dir)
    
    # 获取所有对象ID
    subject_ids = df['eid_ckd'].unique().tolist()
    print(f"共发现 {len(subject_ids)} 个唯一对象")
    
    # 分割数据集
    train_ids, val_ids, test_ids = split_data(subject_ids)
    print(f"数据集分割完成 - 训练集: {len(train_ids)}, 验证集: {len(val_ids)}, 测试集: {len(test_ids)}")
    
    # 建立对象ID到抑郁状态的映射
    subject_depression_map = {}
    for _, row in df.iterrows():
        subject_id = row['eid_ckd']
        subject_depression_map[subject_id] = is_depressed(row)
    
    if eye_type == "left":
       # 处理左眼图像
        print("开始处理左眼图像...")
        for filename in os.listdir(left_dir):
            if filename.endswith(('.jpg', '.jpeg', '.png')):
                subject_id_str = get_subject_id_from_filename(filename)
                try:
                    subject_id = int(subject_id_str)
                except ValueError:
                    print(f"无法解析文件名 {filename} 中的对象ID，跳过该文件")
                    continue

                # 检查该对象是否在我们的Excel数据中
                if subject_id not in subject_depression_map:
                    print(f"对象 {subject_id} 不在Excel数据中，跳过文件 {filename}")
                    continue

                # 确定抑郁状态
                depression = subject_depression_map[subject_id]
                class_dir = 'class_depression' if depression else 'class_non_depression'

                # 确定数据集类型
                if subject_id in train_ids:
                    dataset_dir = 'train'
                elif subject_id in val_ids:
                    dataset_dir = 'val'
                else:
                    dataset_dir = 'test'

                # 构建源路径和目标路径
                src_path = os.path.join(left_dir, filename)
                dest_path = os.path.join(output_dir, dataset_dir, class_dir, f"left_{filename}")

                # 预处理图像
                processed_img = preprocess_image(src_path, target_size)
                if processed_img:
                    # 保存预处理后的图像
                    processed_img.save(dest_path)
                    print(f"已处理并保存: {dest_path}")
                else:
                    print(f"处理失败，跳过文件: {filename}")
    else:
        # 处理右眼图像
        print("开始处理右眼图像...")
        for filename in os.listdir(right_dir):
            if filename.endswith(('.jpg', '.jpeg', '.png')):
                subject_id_str = get_subject_id_from_filename(filename)
                try:
                    subject_id = int(subject_id_str)
                except ValueError:
                    print(f"无法解析文件名 {filename} 中的对象ID，跳过该文件")
                    continue

                # 检查该对象是否在我们的Excel数据中
                if subject_id not in subject_depression_map:
                    print(f"对象 {subject_id} 不在Excel数据中，跳过文件 {filename}")
                    continue

                # 确定抑郁状态
                depression = subject_depression_map[subject_id]
                class_dir = 'class_depression' if depression else 'class_non_depression'

                # 确定数据集类型
                if subject_id in train_ids:
                    dataset_dir = 'train'
                elif subject_id in val_ids:
                    dataset_dir = 'val'
                else:
                    dataset_dir = 'test'

                # 构建源路径和目标路径
                src_path = os.path.join(right_dir, filename)
                dest_path = os.path.join(output_dir, dataset_dir, class_dir, f"right_{filename}")

                # 预处理图像
                processed_img = preprocess_image(src_path, target_size)
                if processed_img:
                    # 保存预处理后的图像
                    processed_img.save(dest_path)
                    print(f"已处理并保存: {dest_path}")
                else:
                    print(f"处理失败，跳过文件: {filename}")
    
    print("图像处理完成！")

if __name__ == "__main__":
    # 配置路径 - 请根据实际情况修改这些路径
    LEFT_IMAGE_DIR = "D:/LingYi/left"          # 左眼图像文件夹路径
    RIGHT_IMAGE_DIR = "D:/LingYi/right"        # 右眼图像文件夹路径
    EYE_TYPE = "Left" # 选择处理左眼图还是右眼图
    EXCEL_PATH = "D:/LingYi/0820_ukb_depression_fundus.xlsx" # Excel文件路径
    OUTPUT_DIR = "D:/LingYi/data_pre_depression_by_left_eye"       # 输出目录路径
    TARGET_SIZE = (224, 224)           # RetFound模型的输入尺寸，可根据需要修改为(384, 384)
    
    # 运行处理函数
    process_images(LEFT_IMAGE_DIR, RIGHT_IMAGE_DIR, EYE_TYPE, EXCEL_PATH, OUTPUT_DIR, TARGET_SIZE)

成功读取Excel文件，共 43445 条记录
创建目录: D:/LingYi/data_pre_depression_by_left_eye\train/class_depression
创建目录: D:/LingYi/data_pre_depression_by_left_eye\train/class_non_depression
创建目录: D:/LingYi/data_pre_depression_by_left_eye\val/class_depression
创建目录: D:/LingYi/data_pre_depression_by_left_eye\val/class_non_depression
创建目录: D:/LingYi/data_pre_depression_by_left_eye\test/class_depression
创建目录: D:/LingYi/data_pre_depression_by_left_eye\test/class_non_depression
共发现 43445 个唯一对象
数据集分割完成 - 训练集: 30411, 验证集: 6517, 测试集: 6517
开始处理左眼图像...
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\val\class_depression\left_1000108_21011_0_0.jpg
对象 1000275 不在Excel数据中，跳过文件 1000275_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1000280_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1000299_21011_0_0.jpg
对象 1000350 不在Excel数据中，跳过文件 1000350_21011_0_0.jpg
对象 1000470 不在Excel数据中，跳过文件 1000470_21011_0_0.jpg
已处理并保存: D:/LingYi/da

已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_depression\left_1007813_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\val\class_depression\left_1007832_21011_0_0.jpg
对象 1007939 不在Excel数据中，跳过文件 1007939_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1007977_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\test\class_depression\left_1008012_21011_0_0.jpg
对象 1008047 不在Excel数据中，跳过文件 1008047_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1008086_21011_0_0.jpg
对象 1008135 不在Excel数据中，跳过文件 1008135_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_depression\left_1008187_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1008241_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1008309_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by

已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\test\class_non_depression\left_1014981_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1014990_21011_0_0.jpg
对象 1015088 不在Excel数据中，跳过文件 1015088_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1015160_21011_0_0.jpg
对象 1015259 不在Excel数据中，跳过文件 1015259_21011_0_0.jpg
对象 1015300 不在Excel数据中，跳过文件 1015300_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1015361_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\val\class_non_depression\left_1015393_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1015407_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\test\class_non_depression\left_1015419_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\val\class_non_depression\left_1015532_21011_0_0.jpg
对象 1015599 不在Excel数据中，跳过文件 

已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1021946_21011_0_0.jpg
对象 1021991 不在Excel数据中，跳过文件 1021991_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1022011_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\val\class_non_depression\left_1022024_21011_0_0.jpg
对象 1022055 不在Excel数据中，跳过文件 1022055_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1022225_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_depression\left_1022504_21011_0_0.jpg
对象 1022529 不在Excel数据中，跳过文件 1022529_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1022537_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1022596_21011_0_0.jpg
对象 1022613 不在Excel数据中，跳过文件 1022613_21011_0_0.jpg
对象 1022703 不在Excel数据中，跳过文件 1022703_21011_0_0.jpg
对象 1022807 不在Excel数据中，跳过文件 102280

已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_depression\left_1030101_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1030376_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1030472_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\test\class_non_depression\left_1030483_21011_0_0.jpg
对象 1030522 不在Excel数据中，跳过文件 1030522_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1030643_21011_0_0.jpg
对象 1030864 不在Excel数据中，跳过文件 1030864_21011_0_0.jpg
对象 1030898 不在Excel数据中，跳过文件 1030898_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\test\class_non_depression\left_1031004_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\test\class_non_depression\left_1031070_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\test\class_non_depression\left_1031107_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_de

...

已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1875945_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1876393_21011_0_0.jpg
对象 1876419 不在Excel数据中，跳过文件 1876419_21011_0_0.jpg
对象 1876463 不在Excel数据中，跳过文件 1876463_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\test\class_depression\left_1876544_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1876604_21011_0_0.jpg
对象 1876727 不在Excel数据中，跳过文件 1876727_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1876773_21011_0_0.jpg
对象 1876868 不在Excel数据中，跳过文件 1876868_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\test\class_non_depression\left_1876879_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1876884_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\val\class_non_depression\left_18

已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1884021_21011_0_0.jpg
对象 1884043 不在Excel数据中，跳过文件 1884043_21011_0_0.jpg
对象 1884148 不在Excel数据中，跳过文件 1884148_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\val\class_non_depression\left_1884259_21011_0_0.jpg
对象 1884264 不在Excel数据中，跳过文件 1884264_21011_0_0.jpg
对象 1884286 不在Excel数据中，跳过文件 1884286_21011_0_0.jpg
对象 1884298 不在Excel数据中，跳过文件 1884298_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1884300_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1884434_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\val\class_non_depression\left_1884526_21011_0_0.jpg
对象 1884567 不在Excel数据中，跳过文件 1884567_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1884629_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\test\class_non_depression\left_18848

已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\test\class_non_depression\left_1893078_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1893147_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_depression\left_1893198_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1893209_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1893283_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1893341_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1893370_21011_0_0.jpg
对象 1893415 不在Excel数据中，跳过文件 1893415_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\test\class_non_depression\left_1893449_21011_0_0.jpg
对象 1893494 不在Excel数据中，跳过文件 1893494_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression

已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1900584_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\val\class_non_depression\left_1900595_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\test\class_non_depression\left_1900638_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1900734_21011_0_0.jpg
对象 1900745 不在Excel数据中，跳过文件 1900745_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1900763_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1900781_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\test\class_non_depression\left_1900813_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1900965_21011_0_0.jpg
对象 1901196 不在Excel数据中，跳过文件 1901196_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depressi

已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1908692_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_depression\left_1908737_21011_0_0.jpg
对象 1908741 不在Excel数据中，跳过文件 1908741_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\val\class_depression\left_1908762_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_depression\left_1908871_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1908956_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\val\class_non_depression\left_1908961_21011_0_0.jpg
对象 1908974 不在Excel数据中，跳过文件 1908974_21011_0_0.jpg
对象 1909165 不在Excel数据中，跳过文件 1909165_21011_0_0.jpg
对象 1909200 不在Excel数据中，跳过文件 1909200_21011_0_0.jpg
对象 1909225 不在Excel数据中，跳过文件 1909225_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_left_eye\train\class_non_depression\left_1909289_21011_0_0.jpg
已处理并保存: D:/LingYi/data_pre_depression_by_le

In [9]:
# 处理左眼或右眼图像并按照三分类抑郁状态和数据集类型分类
import os
import pandas as pd
import random
from sklearn.model_selection import train_test_split
from PIL import Image
import numpy as np

def create_directory_structure(base_dir):
    """创建三分类所需的目录结构"""
    # 定义三分类目录结构：无抑郁、基线抑郁、新发抑郁
    directories = [
        'train/class_0_non_depression',
        'train/class_1_baseline_depression',
        'train/class_2_incident_depression',
        'val/class_0_non_depression',
        'val/class_1_baseline_depression',
        'val/class_2_incident_depression',
        'test/class_0_non_depression',
        'test/class_1_baseline_depression',
        'test/class_2_incident_depression'
    ]
    
    # 创建目录
    for dir_path in directories:
        full_path = os.path.join(base_dir, dir_path)
        os.makedirs(full_path, exist_ok=True)
        print(f"创建目录: {full_path}")

def get_subject_id_from_filename(filename):
    """从文件名中提取对象编号"""
    if '__' in filename:
        return filename.split('__')[0]
    elif '_' in filename:
        return filename.split('_')[0]
    else:
        return os.path.splitext(filename)[0]

def classify_depression(row):
    """
    三分类判断：
    - 0: 无抑郁
    - 1: 基线抑郁（当前有抑郁）
    - 2: 新发抑郁（基线无抑郁，后续出现抑郁）
    """
    # 检查基线抑郁状态
#     baseline_depressed = #(pd.notna(row['new_totdepress']) and row['new_totdepress'] == 1) or \
    baseline_depressed =                    (pd.notna(row['baseline_depression']) and row['baseline_depression'] == '是')
    
    # 检查新发抑郁状态
    incident_depressed = pd.notna(row['incident_depression']) and row['incident_depression'] == '是'
    
    # 三分类逻辑
    if baseline_depressed:
        return 1, 'class_1_baseline_depression'  # 基线抑郁
    elif not baseline_depressed and incident_depressed:
        return 2, 'class_2_incident_depression'  # 新发抑郁
    else:
        return 0, 'class_0_non_depression'       # 无抑郁

def split_data(subject_ids, train_ratio=0.7, val_ratio=0.15, test_ratio=0.15):
    """将数据分割为训练集、验证集和测试集"""
    if not np.isclose(train_ratio + val_ratio + test_ratio, 1.0):
        raise ValueError("训练集、验证集和测试集的比例之和必须为1.0")
    
    # 先分割训练集和临时集
    train_ids, temp_ids = train_test_split(
        subject_ids, 
        test_size=1-train_ratio, 
        random_state=42
    )
    
    # 分割验证集和测试集
    val_proportion = val_ratio / (val_ratio + test_ratio)
    val_ids, test_ids = train_test_split(
        temp_ids, 
        test_size=1-val_proportion, 
        random_state=42
    )
    
    return train_ids, val_ids, test_ids

def preprocess_image(image_path, target_size=(224, 224)):
    """预处理视网膜图像以适应RetFound模型"""
    try:
        with Image.open(image_path) as img:
            # 转换为RGB格式
            if img.mode != 'RGB':
                img = img.convert('RGB')
            
            # 保持纵横比调整大小
            width, height = img.size
            target_width, target_height = target_size
            
            ratio = min(target_width / width, target_height / height)
            new_width = int(width * ratio)
            new_height = int(height * ratio)
            
            img = img.resize((new_width, new_height), Image.LANCZOS)
            
            # 中心裁剪到目标尺寸
            left = (new_width - target_width) // 2
            top = (new_height - target_height) // 2
            right = left + target_width
            bottom = top + target_height
            
            return img.crop((left, top, right, bottom))
    except Exception as e:
        print(f"预处理图像 {image_path} 时出错: {str(e)}")
        return None

def process_left_eye_images(left_dir, excel_path, output_dir, target_size=(224, 224)):
    """处理左眼图像并按照三分类抑郁状态和数据集类型分类"""
    # 读取Excel文件
    df = pd.read_excel(excel_path)
    print(f"成功读取Excel文件，共 {len(df)} 条记录")
    
    # 创建目录结构
    create_directory_structure(output_dir)
    
    # 获取所有对象ID并去重
    subject_ids = df['eid_ckd'].dropna().unique().tolist()
    print(f"共发现 {len(subject_ids)} 个唯一对象")
    
    # 分割数据集
    train_ids, val_ids, test_ids = split_data(subject_ids)
    print(f"数据集分割完成 - 训练集: {len(train_ids)}, 验证集: {len(val_ids)}, 测试集: {len(test_ids)}")
    
    # 建立对象ID到抑郁状态的映射
    subject_depression_map = {}
    class_count = {0: 0, 1: 0, 2: 0}  # 统计每个类别的数量
    
    for _, row in df.iterrows():
        subject_id = row['eid_ckd']
        if pd.notna(subject_id):
            class_id, class_name = classify_depression(row)
            subject_depression_map[subject_id] = {
                'class_id': class_id,
                'class_name': class_name
            }
            class_count[class_id] += 1
    
    # 打印类别分布
    print(f"类别分布统计:")
    print(f"0: 无抑郁 - {class_count[0]}人")
    print(f"1: 基线抑郁 - {class_count[1]}人")
    print(f"2: 新发抑郁 - {class_count[2]}人")
    
    # 处理左眼图像
    print("\n开始处理左眼图像...")
    processed_count = 0
    skipped_count = 0
    
    if not os.path.exists(left_dir):
        print(f"错误: 左眼图像目录不存在 - {left_dir}")
        return
    
    for filename in os.listdir(left_dir):
        # 只处理图像文件
        if not filename.lower().endswith(('.jpg', '.jpeg', '.png', '.bmp', '.tiff')):
            skipped_count += 1
            continue
            
        subject_id_str = get_subject_id_from_filename(filename)
        try:
            subject_id = int(subject_id_str)
        except ValueError:
            print(f"无法解析文件名 {filename} 中的对象ID，跳过该文件")
            skipped_count += 1
            continue
            
        # 检查该对象是否在我们的Excel数据中
        if subject_id not in subject_depression_map:
            print(f"对象 {subject_id} 不在Excel数据中，跳过文件 {filename}")
            skipped_count += 1
            continue
            
        # 获取分类信息
        dep_info = subject_depression_map[subject_id]
        class_dir = dep_info['class_name']
        
        # 确定数据集类型
        if subject_id in train_ids:
            dataset_dir = 'train'
        elif subject_id in val_ids:
            dataset_dir = 'val'
        else:
            dataset_dir = 'test'
        
        # 构建源路径和目标路径
        src_path = os.path.join(left_dir, filename)
        dest_filename = f"left_{filename}"
        dest_path = os.path.join(output_dir, dataset_dir, class_dir, dest_filename)
        
        # 预处理图像
        processed_img = preprocess_image(src_path, target_size)
        if processed_img:
            processed_img.save(dest_path)
            processed_count += 1
            if processed_count % 100 == 0:
                print(f"已处理 {processed_count} 张图像...")
        else:
            print(f"处理失败，跳过文件: {filename}")
            skipped_count += 1
    
    print(f"\n图像处理完成！共处理 {processed_count} 张图像，跳过 {skipped_count} 张图像")
    print(f"输出目录: {output_dir}")

if __name__ == "__main__":
    # 配置路径 - 请根据实际情况修改这些路径
    LEFT_IMAGE_DIR = "D:/LingYi/left"          # 左眼图像文件夹路径
    EXCEL_PATH = "D:/LingYi/0820_ukb_depression_fundus.xlsx" # Excel文件路径
    OUTPUT_DIR = "D:/LingYi/data_pre_depression_by_left_eye_three_class"  # 输出目录路径
    TARGET_SIZE = (224, 224)  # RetFound模型的输入尺寸
    
    # 运行处理函数（仅处理左眼图像）
    process_left_eye_images(LEFT_IMAGE_DIR, EXCEL_PATH, OUTPUT_DIR, TARGET_SIZE)
    

成功读取Excel文件，共 43445 条记录
创建目录: D:/LingYi/data_pre_depression_by_left_eye_three_class\train/class_0_non_depression
创建目录: D:/LingYi/data_pre_depression_by_left_eye_three_class\train/class_1_baseline_depression
创建目录: D:/LingYi/data_pre_depression_by_left_eye_three_class\train/class_2_incident_depression
创建目录: D:/LingYi/data_pre_depression_by_left_eye_three_class\val/class_0_non_depression
创建目录: D:/LingYi/data_pre_depression_by_left_eye_three_class\val/class_1_baseline_depression
创建目录: D:/LingYi/data_pre_depression_by_left_eye_three_class\val/class_2_incident_depression
创建目录: D:/LingYi/data_pre_depression_by_left_eye_three_class\test/class_0_non_depression
创建目录: D:/LingYi/data_pre_depression_by_left_eye_three_class\test/class_1_baseline_depression
创建目录: D:/LingYi/data_pre_depression_by_left_eye_three_class\test/class_2_incident_depression
共发现 43445 个唯一对象
数据集分割完成 - 训练集: 30411, 验证集: 6517, 测试集: 6517
类别分布统计:
0: 无抑郁 - 39503人
1: 基线抑郁 - 2540人
2: 新发抑郁 - 1402人

开始处理左眼图像...
对象 1000275 不在Excel数据中，跳过文件

In [3]:
# 左眼或右眼图片提取并数据增强少数类
import os
from torchvision import transforms
import pandas as pd
import shutil
import random
from sklearn.model_selection import train_test_split
from PIL import Image
import numpy as np
  # 新增：用于数据增强

def create_directory_structure(base_dir):
    """创建所需的目录结构"""
    directories = [
        'train/class_depression',
        'train/class_non_depression',
        'val/class_depression',
        'val/class_non_depression',
        'test/class_depression',
        'test/class_non_depression'
    ]
    
    for dir_path in directories:
        full_path = os.path.join(base_dir, dir_path)
        os.makedirs(full_path, exist_ok=True)
        print(f"创建目录: {full_path}")

def get_subject_id_from_filename(filename):
    """从文件名中提取对象编号"""
    if '__' in filename:
        return filename.split('__')[0]
    else:
        return filename.split('_')[0]

def is_depressed(row):
    """判断对象是否有抑郁症状"""
    if (row['new_totdepress'] == 1 or 
        row['baseline_depression'] == '是' or 
        row['incident_depression'] == '是'):
        return True
    return False

def split_data(subject_ids, train_ratio=0.7, val_ratio=0.15, test_ratio=0.15):
    """将数据分割为训练集、验证集和测试集"""
    train_ids, temp_ids = train_test_split(subject_ids, test_size=1-train_ratio, random_state=42)
    val_proportion = val_ratio / (val_ratio + test_ratio)
    val_ids, test_ids = train_test_split(temp_ids, test_size=1-val_proportion, random_state=42)
    return train_ids, val_ids, test_ids

def preprocess_image(image_path, target_size=(224, 224)):
    """预处理视网膜图像（基础版： resize+中心裁剪+转RGB）"""
    try:
        with Image.open(image_path) as img:
            if img.mode != 'RGB':
                img = img.convert('RGB')
            
            # 保持纵横比缩放后中心裁剪
            width, height = img.size
            target_width, target_height = target_size
            ratio = min(target_width / width, target_height / height)
            new_width, new_height = int(width * ratio), int(height * ratio)
            img = img.resize((new_width, new_height), Image.LANCZOS)
            
            left = (new_width - target_width) // 2
            top = (new_height - target_height) // 2
            img = img.crop((left, top, left+target_width, top+target_height))
            return img
    except Exception as e:
        print(f"预处理图像 {image_path} 出错: {str(e)}")
        return None

def get_minority_aug_transform(target_size=(224, 224)):
    """新增：少数类（抑郁）专属增强变换（生成多样化样本）"""
    return transforms.Compose([
#         transforms.RandomHorizontalFlip(p=0.5),  # 随机水平翻转（视网膜左右对称）
#         transforms.RandomRotation(degrees=(-5, 5)),  # 小角度旋转（避免视盘失真）
        transforms.ColorJitter(brightness=0.2, contrast=0.2, saturation=0.1),  # 色彩调整
#         transforms.RandomApply([transforms.GaussianBlur(kernel_size=3, sigma=(0.1, 0.3))], p=0.4),  # 轻度模糊
        transforms.Resize(target_size),  # 确保尺寸一致
#         transforms.ToTensor()  # 转Tensor（后续保存时需转回PIL）
    ])

def tensor_to_pil(tensor_img):
    """新增：将Tensor图像转回PIL Image（用于保存增强样本）"""
    transform = transforms.ToPILImage()
    return transform(tensor_img)

def count_class_samples(base_dir, dataset_type):
    """新增：统计指定数据集（train/val/test）的各类别数量"""
    depression_dir = os.path.join(base_dir, dataset_type, 'class_depression')
    non_depression_dir = os.path.join(base_dir, dataset_type, 'class_non_depression')
    
    # 统计文件数量（排除隐藏文件）
    depression_count = len([f for f in os.listdir(depression_dir) if not f.startswith('.')])
    non_depression_count = len([f for f in os.listdir(non_depression_dir) if not f.startswith('.')])
    total = depression_count + non_depression_count
    ratio = f"{depression_count}:{non_depression_count}" if non_depression_count !=0 else "N/A"
    
    print(f"\n{dataset_type}集统计:")
    print(f"- 抑郁类（class_depression）: {depression_count} 个")
    print(f"- 非抑郁类（class_non_depression）: {non_depression_count} 个")
    print(f"- 总样本数: {total} 个")
    print(f"- 类别比例: {ratio}（少数类:多数类）")
    
    return depression_count, non_depression_count

def augment_minority_to_ratio(base_dir, target_ratio=1/3):
    """新增：对训练集少数类（抑郁）增强，目标比例（少数类/多数类=target_ratio，即1:3）"""
    train_depression_dir = os.path.join(base_dir, 'train', 'class_depression')
    train_non_depression_dir = os.path.join(base_dir, 'train', 'class_non_depression')
    
    # 1. 获取当前训练集类别数量
    dep_count, non_dep_count = count_class_samples(base_dir, 'train')
    if dep_count ==0 or non_dep_count ==0:
        print("训练集类别数量异常，跳过增强")
        return
    
    # 2. 计算目标少数类数量（目标比例=少数类/多数类=1/3 → 目标少数类数=多数类数×1/3）
    target_dep_count = int(non_dep_count * target_ratio)
    if dep_count >= target_dep_count:
        print(f"少数类已满足目标比例（当前{dep_count}个 ≥ 目标{target_dep_count}个），跳过增强")
        return
    
    # 3. 计算需新增的增强样本数量
    need_aug_count = target_dep_count - dep_count
    print(f"\n开始增强少数类：需新增 {need_aug_count} 个抑郁类样本（目标比例1:3）")
    
    # 4. 获取原始少数类样本路径
    original_dep_files = [f for f in os.listdir(train_depression_dir) if not f.startswith('.')]
    if len(original_dep_files) ==0:
        print("无原始少数类样本，跳过增强")
        return
    
    # 5. 定义增强变换
    aug_transform = get_minority_aug_transform(target_size=(224,224))
    
    # 6. 生成增强样本并保存
    for i in range(need_aug_count):
        # 随机选择一个原始样本
        random_file = random.choice(original_dep_files)
        original_path = os.path.join(train_depression_dir, random_file)
        
        # 读取原始图像并预处理
        original_img = preprocess_image(original_path)
        if original_img is None:
            continue
        
        # 应用增强（需先转Tensor，增强后转回PIL）
        tensor_img = transforms.ToTensor()(original_img)  # 转Tensor
        augmented_tensor = aug_transform(tensor_img)     # 增强
        augmented_img = tensor_to_pil(augmented_tensor)  # 转回PIL
        
        # 定义增强样本文件名（避免重复）
        aug_filename = f"aug_{i+1}_{random_file}"
        aug_save_path = os.path.join(train_depression_dir, aug_filename)
        
        # 保存增强样本
        augmented_img.save(aug_save_path)
        if (i+1) % 50 ==0:  # 每增强50个打印一次进度
            print(f"已增强 {i+1}/{need_aug_count} 个少数类样本")
    
    # 7. 增强后重新统计
    print("\n少数类增强完成，增强后训练集统计:")
    count_class_samples(base_dir, 'train')

def process_images(left_dir, right_dir, eye_type, excel_path, output_dir, target_size=(224, 224)):
    """主函数：处理图像+分类存储+统计+少数类增强"""
    # 1. 读取Excel并创建目录
    df = pd.read_excel(excel_path)
    print(f"成功读取Excel文件，共 {len(df)} 条记录")
    create_directory_structure(output_dir)
    
    # 2. 分割数据集（按对象ID）
    subject_ids = df['eid_ckd'].unique().tolist()
    print(f"共发现 {len(subject_ids)} 个唯一对象")
    train_ids, val_ids, test_ids = split_data(subject_ids)
    print(f"数据集分割完成 - 训练集: {len(train_ids)}, 验证集: {len(val_ids)}, 测试集: {len(test_ids)}")
    
    # 3. 建立对象ID→抑郁状态的映射
    subject_depression_map = {}
    for _, row in df.iterrows():
        subject_id = row['eid_ckd']
        subject_depression_map[subject_id] = is_depressed(row)
    
    if eye_type == "left":
        # 4. 处理左眼图像（训练集/验证集/测试集）
        print("\n开始处理左眼图像...")
        for filename in os.listdir(left_dir):
            if filename.endswith(('.jpg', '.jpeg', '.png')):
                subject_id_str = get_subject_id_from_filename(filename)
                try:
                    subject_id = int(subject_id_str)
                except ValueError:
                    print(f"无法解析文件名 {filename} 中的对象ID，跳过")
                    continue

                if subject_id not in subject_depression_map:
                    print(f"对象 {subject_id} 不在Excel中，跳过文件 {filename}")
                    continue

                # 确定类别和数据集类型
                depression = subject_depression_map[subject_id]
                class_dir = 'class_depression' if depression else 'class_non_depression'
                if subject_id in train_ids:
                    dataset_dir = 'train'
                elif subject_id in val_ids:
                    dataset_dir = 'val'
                else:
                    dataset_dir = 'test'

                # 预处理并保存
                src_path = os.path.join(left_dir, filename)
                dest_path = os.path.join(output_dir, dataset_dir, class_dir, f"left_{filename}")
                processed_img = preprocess_image(src_path, target_size)
                if processed_img:
                    processed_img.save(dest_path)
                    # 每处理100个打印一次进度
                    if len([f for f in os.listdir(os.path.join(output_dir, dataset_dir, class_dir)) if not f.startswith('.')]) % 100 ==0:
                        print(f"已处理 {dataset_dir}/{class_dir}: {len([f for f in os.listdir(os.path.join(output_dir, dataset_dir, class_dir)) if not f.startswith('.')])} 个样本")
                else:
                    print(f"处理失败，跳过 {filename}")
    else:           
        print("\n开始处理右眼图像...")
        for filename in os.listdir(right_dir):
            if filename.endswith(('.jpg', '.jpeg', '.png')):
                subject_id_str = get_subject_id_from_filename(filename)
                try:
                    subject_id = int(subject_id_str)
                except ValueError:
                    print(f"无法解析文件名 {filename} 中的对象ID，跳过")
                    continue

                if subject_id not in subject_depression_map:
                    print(f"对象 {subject_id} 不在Excel中，跳过文件 {filename}")
                    continue

                # 确定类别和数据集类型
                depression = subject_depression_map[subject_id]
                class_dir = 'class_depression' if depression else 'class_non_depression'
                if subject_id in train_ids:
                    dataset_dir = 'train'
                elif subject_id in val_ids:
                    dataset_dir = 'val'
                else:
                    dataset_dir = 'test'

                # 预处理并保存
                src_path = os.path.join(right_dir, filename)
                dest_path = os.path.join(output_dir, dataset_dir, class_dir, f"right_{filename}")
                processed_img = preprocess_image(src_path, target_size)
                if processed_img:
                    processed_img.save(dest_path)
                    # 每处理100个打印一次进度
                    if len([f for f in os.listdir(os.path.join(output_dir, dataset_dir, class_dir)) if not f.startswith('.')]) % 100 ==0:
                        print(f"已处理 {dataset_dir}/{class_dir}: {len([f for f in os.listdir(os.path.join(output_dir, dataset_dir, class_dir)) if not f.startswith('.')])} 个样本")
                else:
                    print(f"处理失败，跳过 {filename}")       
    
    # 5. 统计所有数据集的初始类别数量
    print("\n=== 初始类别数量统计 ===")
    count_class_samples(output_dir, 'train')
    count_class_samples(output_dir, 'val')
    count_class_samples(output_dir, 'test')
    
    # 6. 仅对训练集少数类进行增强（目标1:3比例）
    print("\n=== 开始训练集少数类增强 ===")
    augment_minority_to_ratio(output_dir, target_ratio=2/3)  # target_ratio=1/3 → 1:3比例
    
    print("\n所有图像处理与增强任务完成！")

if __name__ == "__main__":
    # 配置路径（请根据实际情况修改）
    LEFT_IMAGE_DIR = "D:/LingYi/left"          
    RIGHT_IMAGE_DIR = "D:/LingYi/right"
    EYE_TYPE = "Left" # 选择处理左眼图还是右眼图
    EXCEL_PATH = "D:/LingYi/0820_ukb_depression_fundus.xlsx" 
    OUTPUT_DIR = "D:/LingYi/data_pre_depression_by_left_eye_enhance"       
    TARGET_SIZE = (224, 224)  # RetFound输入尺寸
    
    # 运行
    process_images(LEFT_IMAGE_DIR, RIGHT_IMAGE_DIR, EYE_TYPE, EXCEL_PATH, OUTPUT_DIR, TARGET_SIZE)

成功读取Excel文件，共 43445 条记录
创建目录: D:/LingYi/data_pre_depression_by_right_eye_enhance\train/class_depression
创建目录: D:/LingYi/data_pre_depression_by_right_eye_enhance\train/class_non_depression
创建目录: D:/LingYi/data_pre_depression_by_right_eye_enhance\val/class_depression
创建目录: D:/LingYi/data_pre_depression_by_right_eye_enhance\val/class_non_depression
创建目录: D:/LingYi/data_pre_depression_by_right_eye_enhance\test/class_depression
创建目录: D:/LingYi/data_pre_depression_by_right_eye_enhance\test/class_non_depression
共发现 43445 个唯一对象
数据集分割完成 - 训练集: 30411, 验证集: 6517, 测试集: 6517

开始处理右眼图像...
对象 1000275 不在Excel中，跳过文件 1000275_21013_0_0.jpg
对象 1000350 不在Excel中，跳过文件 1000350_21013_0_0.jpg
对象 1000470 不在Excel中，跳过文件 1000470_21013_0_0.jpg
对象 1000822 不在Excel中，跳过文件 1000822_21013_0_0.jpg
对象 1000979 不在Excel中，跳过文件 1000979_21013_0_0.jpg
对象 1001541 不在Excel中，跳过文件 1001541_21013_0_0.jpg
对象 1001553 不在Excel中，跳过文件 1001553_21013_0_0.jpg
对象 1001585 不在Excel中，跳过文件 1001585_21013_0_0.jpg
对象 1002298 不在Excel中，跳过文件 1002298_21013_0_0

对象 1040076 不在Excel中，跳过文件 1040076_21013_0_0.jpg
对象 1040701 不在Excel中，跳过文件 1040701_21013_0_0.jpg
对象 1041013 不在Excel中，跳过文件 1041013_21013_0_0.jpg
对象 1041263 不在Excel中，跳过文件 1041263_21013_0_0.jpg
对象 1041276 不在Excel中，跳过文件 1041276_21013_0_0.jpg
对象 1041281 不在Excel中，跳过文件 1041281_21013_0_0.jpg
对象 1041412 不在Excel中，跳过文件 1041412_21013_0_0.jpg
对象 1041471 不在Excel中，跳过文件 1041471_21013_0_0.jpg
对象 1041756 不在Excel中，跳过文件 1041756_21013_0_0.jpg
对象 1041761 不在Excel中，跳过文件 1041761_21013_0_0.jpg
对象 1041774 不在Excel中，跳过文件 1041774_21013_0_0.jpg
对象 1041809 不在Excel中，跳过文件 1041809_21013_0_0.jpg
对象 1041811 不在Excel中，跳过文件 1041811_21013_0_0.jpg
对象 1042208 不在Excel中，跳过文件 1042208_21013_0_0.jpg
对象 1042227 不在Excel中，跳过文件 1042227_21013_0_0.jpg
对象 1042307 不在Excel中，跳过文件 1042307_21013_0_0.jpg
对象 1042436 不在Excel中，跳过文件 1042436_21013_0_0.jpg
对象 1043009 不在Excel中，跳过文件 1043009_21013_0_0.jpg
对象 1043011 不在Excel中，跳过文件 1043011_21013_0_0.jpg
对象 1043518 不在Excel中，跳过文件 1043518_21013_0_0.jpg
对象 1043658 不在Excel中，跳过文件 1043658_21013_0_0.jpg
对象 1043966 不在

对象 1076443 不在Excel中，跳过文件 1076443_21013_0_0.jpg
对象 1076477 不在Excel中，跳过文件 1076477_21013_0_0.jpg
对象 1076551 不在Excel中，跳过文件 1076551_21013_0_0.jpg
对象 1076732 不在Excel中，跳过文件 1076732_21013_0_0.jpg
对象 1077345 不在Excel中，跳过文件 1077345_21013_0_0.jpg
对象 1077390 不在Excel中，跳过文件 1077390_21013_0_0.jpg
对象 1077785 不在Excel中，跳过文件 1077785_21013_0_0.jpg
对象 1078985 不在Excel中，跳过文件 1078985_21013_0_0.jpg
对象 1079324 不在Excel中，跳过文件 1079324_21013_0_0.jpg
对象 1079360 不在Excel中，跳过文件 1079360_21013_0_0.jpg
对象 1080145 不在Excel中，跳过文件 1080145_21013_0_0.jpg
对象 1080597 不在Excel中，跳过文件 1080597_21013_0_0.jpg
对象 1081047 不在Excel中，跳过文件 1081047_21013_0_0.jpg
对象 1081229 不在Excel中，跳过文件 1081229_21013_0_0.jpg
对象 1081253 不在Excel中，跳过文件 1081253_21013_0_0.jpg
对象 1081311 不在Excel中，跳过文件 1081311_21013_0_0.jpg
对象 1081324 不在Excel中，跳过文件 1081324_21013_0_0.jpg
对象 1082069 不在Excel中，跳过文件 1082069_21013_0_0.jpg
对象 1082260 不在Excel中，跳过文件 1082260_21013_0_0.jpg
对象 1082304 不在Excel中，跳过文件 1082304_21013_0_0.jpg
对象 1082370 不在Excel中，跳过文件 1082370_21013_0_0.jpg
对象 1082396 不在

对象 1117621 不在Excel中，跳过文件 1117621_21013_0_0.jpg
对象 1117833 不在Excel中，跳过文件 1117833_21013_0_0.jpg
对象 1117864 不在Excel中，跳过文件 1117864_21013_0_0.jpg
对象 1117886 不在Excel中，跳过文件 1117886_21013_0_0.jpg
对象 1118123 不在Excel中，跳过文件 1118123_21013_0_0.jpg
对象 1118276 不在Excel中，跳过文件 1118276_21013_0_0.jpg
对象 1119110 不在Excel中，跳过文件 1119110_21013_0_0.jpg
对象 1119593 不在Excel中，跳过文件 1119593_21013_0_0.jpg
对象 1120274 不在Excel中，跳过文件 1120274_21013_0_0.jpg
对象 1120398 不在Excel中，跳过文件 1120398_21013_0_0.jpg
对象 1120479 不在Excel中，跳过文件 1120479_21013_0_0.jpg
对象 1120562 不在Excel中，跳过文件 1120562_21013_0_0.jpg
对象 1120658 不在Excel中，跳过文件 1120658_21013_0_0.jpg
对象 1120735 不在Excel中，跳过文件 1120735_21013_0_0.jpg
对象 1121482 不在Excel中，跳过文件 1121482_21013_0_0.jpg
对象 1121906 不在Excel中，跳过文件 1121906_21013_0_0.jpg
对象 1121914 不在Excel中，跳过文件 1121914_21013_0_0.jpg
对象 1121977 不在Excel中，跳过文件 1121977_21013_0_0.jpg
对象 1122154 不在Excel中，跳过文件 1122154_21013_0_0.jpg
对象 1122355 不在Excel中，跳过文件 1122355_21013_0_0.jpg
对象 1122721 不在Excel中，跳过文件 1122721_21013_0_0.jpg
对象 1123001 不在

对象 1155648 不在Excel中，跳过文件 1155648_21013_0_0.jpg
对象 1156013 不在Excel中，跳过文件 1156013_21013_0_0.jpg
对象 1156366 不在Excel中，跳过文件 1156366_21013_0_0.jpg
对象 1157066 不在Excel中，跳过文件 1157066_21013_0_0.jpg
对象 1157100 不在Excel中，跳过文件 1157100_21013_0_0.jpg
对象 1157221 不在Excel中，跳过文件 1157221_21013_0_0.jpg
对象 1157239 不在Excel中，跳过文件 1157239_21013_0_0.jpg
对象 1157292 不在Excel中，跳过文件 1157292_21013_0_0.jpg
对象 1157723 不在Excel中，跳过文件 1157723_21013_0_0.jpg
对象 1157768 不在Excel中，跳过文件 1157768_21013_0_0.jpg
对象 1157779 不在Excel中，跳过文件 1157779_21013_0_0.jpg
对象 1157983 不在Excel中，跳过文件 1157983_21013_0_0.jpg
对象 1158470 不在Excel中，跳过文件 1158470_21013_0_0.jpg
对象 1158736 不在Excel中，跳过文件 1158736_21013_0_0.jpg
对象 1158810 不在Excel中，跳过文件 1158810_21013_0_0.jpg
对象 1158846 不在Excel中，跳过文件 1158846_21013_0_0.jpg
对象 1159053 不在Excel中，跳过文件 1159053_21013_0_0.jpg
对象 1159257 不在Excel中，跳过文件 1159257_21013_0_0.jpg
对象 1159456 不在Excel中，跳过文件 1159456_21013_0_0.jpg
对象 1159548 不在Excel中，跳过文件 1159548_21013_0_0.jpg
对象 1159630 不在Excel中，跳过文件 1159630_21013_0_0.jpg
对象 1159877 不在

...

对象 1734061 不在Excel中，跳过文件 1734061_21013_0_0.jpg
对象 1734130 不在Excel中，跳过文件 1734130_21013_0_0.jpg
对象 1734194 不在Excel中，跳过文件 1734194_21013_0_0.jpg
对象 1734267 不在Excel中，跳过文件 1734267_21013_0_0.jpg
对象 1734441 不在Excel中，跳过文件 1734441_21013_0_0.jpg
对象 1734520 不在Excel中，跳过文件 1734520_21013_0_0.jpg
对象 1734878 不在Excel中，跳过文件 1734878_21013_0_0.jpg
对象 1735440 不在Excel中，跳过文件 1735440_21013_0_0.jpg
对象 1735807 不在Excel中，跳过文件 1735807_21013_0_0.jpg
对象 1735863 不在Excel中，跳过文件 1735863_21013_0_0.jpg
对象 1736133 不在Excel中，跳过文件 1736133_21013_0_0.jpg
对象 1736595 不在Excel中，跳过文件 1736595_21013_0_0.jpg
对象 1736674 不在Excel中，跳过文件 1736674_21013_0_0.jpg
对象 1736689 不在Excel中，跳过文件 1736689_21013_0_0.jpg
对象 1736776 不在Excel中，跳过文件 1736776_21013_0_0.jpg
对象 1736977 不在Excel中，跳过文件 1736977_21013_0_0.jpg
对象 1737279 不在Excel中，跳过文件 1737279_21013_0_0.jpg
对象 1737442 不在Excel中，跳过文件 1737442_21013_0_0.jpg
对象 1738713 不在Excel中，跳过文件 1738713_21013_0_0.jpg
对象 1738817 不在Excel中，跳过文件 1738817_21013_0_0.jpg
对象 1738889 不在Excel中，跳过文件 1738889_21013_0_0.jpg
对象 1739065 不在

对象 1771481 不在Excel中，跳过文件 1771481_21013_0_0.jpg
已处理 val/class_non_depression: 900 个样本
对象 1771794 不在Excel中，跳过文件 1771794_21013_0_0.jpg
对象 1772114 不在Excel中，跳过文件 1772114_21013_0_0.jpg
对象 1772225 不在Excel中，跳过文件 1772225_21013_0_0.jpg
对象 1772658 不在Excel中，跳过文件 1772658_21013_0_0.jpg
对象 1772746 不在Excel中，跳过文件 1772746_21013_0_0.jpg
对象 1773334 不在Excel中，跳过文件 1773334_21013_0_0.jpg
对象 1773503 不在Excel中，跳过文件 1773503_21013_0_0.jpg
对象 1773522 不在Excel中，跳过文件 1773522_21013_0_0.jpg
对象 1773606 不在Excel中，跳过文件 1773606_21013_0_0.jpg
对象 1773704 不在Excel中，跳过文件 1773704_21013_0_0.jpg
对象 1774209 不在Excel中，跳过文件 1774209_21013_0_0.jpg
对象 1775406 不在Excel中，跳过文件 1775406_21013_0_0.jpg
对象 1775488 不在Excel中，跳过文件 1775488_21013_0_0.jpg
对象 1775566 不在Excel中，跳过文件 1775566_21013_0_0.jpg
对象 1775672 不在Excel中，跳过文件 1775672_21013_0_0.jpg
对象 1775683 不在Excel中，跳过文件 1775683_21013_0_0.jpg
对象 1775697 不在Excel中，跳过文件 1775697_21013_0_0.jpg
对象 1775905 不在Excel中，跳过文件 1775905_21013_0_0.jpg
对象 1776382 不在Excel中，跳过文件 1776382_21013_0_0.jpg
对象 1776486 不在Excel中，跳过

对象 1811077 不在Excel中，跳过文件 1811077_21013_0_0.jpg
对象 1811356 不在Excel中，跳过文件 1811356_21013_0_0.jpg
对象 1811445 不在Excel中，跳过文件 1811445_21013_0_0.jpg
对象 1811481 不在Excel中，跳过文件 1811481_21013_0_0.jpg
对象 1811685 不在Excel中，跳过文件 1811685_21013_0_0.jpg
对象 1811751 不在Excel中，跳过文件 1811751_21013_0_0.jpg
对象 1811978 不在Excel中，跳过文件 1811978_21013_0_0.jpg
对象 1812048 不在Excel中，跳过文件 1812048_21013_0_0.jpg
对象 1812305 不在Excel中，跳过文件 1812305_21013_0_0.jpg
对象 1812518 不在Excel中，跳过文件 1812518_21013_0_0.jpg
对象 1812746 不在Excel中，跳过文件 1812746_21013_0_0.jpg
对象 1812769 不在Excel中，跳过文件 1812769_21013_0_0.jpg
对象 1812819 不在Excel中，跳过文件 1812819_21013_0_0.jpg
对象 1812828 不在Excel中，跳过文件 1812828_21013_0_0.jpg
对象 1813101 不在Excel中，跳过文件 1813101_21013_0_0.jpg
对象 1813363 不在Excel中，跳过文件 1813363_21013_0_0.jpg
对象 1813677 不在Excel中，跳过文件 1813677_21013_0_0.jpg
对象 1814003 不在Excel中，跳过文件 1814003_21013_0_0.jpg
对象 1814105 不在Excel中，跳过文件 1814105_21013_0_0.jpg
对象 1814283 不在Excel中，跳过文件 1814283_21013_0_0.jpg
对象 1814557 不在Excel中，跳过文件 1814557_21013_0_0.jpg
对象 1814625 不在

对象 1846780 不在Excel中，跳过文件 1846780_21013_0_0.jpg
对象 1846889 不在Excel中，跳过文件 1846889_21013_0_0.jpg
对象 1847079 不在Excel中，跳过文件 1847079_21013_0_0.jpg
对象 1847448 不在Excel中，跳过文件 1847448_21013_0_0.jpg
对象 1847483 不在Excel中，跳过文件 1847483_21013_0_0.jpg
对象 1847587 不在Excel中，跳过文件 1847587_21013_0_0.jpg
对象 1848366 不在Excel中，跳过文件 1848366_21013_0_0.jpg
对象 1848918 不在Excel中，跳过文件 1848918_21013_0_0.jpg
对象 1848937 不在Excel中，跳过文件 1848937_21013_0_0.jpg
对象 1849047 不在Excel中，跳过文件 1849047_21013_0_0.jpg
对象 1849383 不在Excel中，跳过文件 1849383_21013_0_0.jpg
对象 1849815 不在Excel中，跳过文件 1849815_21013_0_0.jpg
对象 1850107 不在Excel中，跳过文件 1850107_21013_0_0.jpg
对象 1850190 不在Excel中，跳过文件 1850190_21013_0_0.jpg
对象 1851178 不在Excel中，跳过文件 1851178_21013_0_0.jpg
对象 1851218 不在Excel中，跳过文件 1851218_21013_0_0.jpg
对象 1851574 不在Excel中，跳过文件 1851574_21013_0_0.jpg
对象 1851695 不在Excel中，跳过文件 1851695_21013_0_0.jpg
对象 1851765 不在Excel中，跳过文件 1851765_21013_0_0.jpg
对象 1852069 不在Excel中，跳过文件 1852069_21013_0_0.jpg
对象 1852318 不在Excel中，跳过文件 1852318_21013_0_0.jpg
对象 1852370 不在

对象 1884567 不在Excel中，跳过文件 1884567_21013_0_0.jpg
对象 1885265 不在Excel中，跳过文件 1885265_21013_0_0.jpg
对象 1885612 不在Excel中，跳过文件 1885612_21013_0_0.jpg
对象 1885804 不在Excel中，跳过文件 1885804_21013_0_0.jpg
对象 1886040 不在Excel中，跳过文件 1886040_21013_0_0.jpg
对象 1886334 不在Excel中，跳过文件 1886334_21013_0_0.jpg
对象 1886591 不在Excel中，跳过文件 1886591_21013_0_0.jpg
对象 1887118 不在Excel中，跳过文件 1887118_21013_0_0.jpg
对象 1887406 不在Excel中，跳过文件 1887406_21013_0_0.jpg
对象 1887477 不在Excel中，跳过文件 1887477_21013_0_0.jpg
对象 1887527 不在Excel中，跳过文件 1887527_21013_0_0.jpg
对象 1887573 不在Excel中，跳过文件 1887573_21013_0_0.jpg
对象 1887624 不在Excel中，跳过文件 1887624_21013_0_0.jpg
对象 1887726 不在Excel中，跳过文件 1887726_21013_0_0.jpg
已处理 test/class_non_depression: 1000 个样本
对象 1888474 不在Excel中，跳过文件 1888474_21013_0_0.jpg
对象 1888548 不在Excel中，跳过文件 1888548_21013_0_0.jpg
对象 1888850 不在Excel中，跳过文件 1888850_21013_0_0.jpg
对象 1889496 不在Excel中，跳过文件 1889496_21013_0_0.jpg
对象 1889512 不在Excel中，跳过文件 1889512_21013_0_0.jpg
对象 1889607 不在Excel中，跳过文件 1889607_21013_0_0.jpg
对象 1889676 不在Excel中，

In [1]:
# 选择提取双眼图片

import os
import pandas as pd
import shutil
import random
from sklearn.model_selection import train_test_split
from PIL import Image
import numpy as np

def create_directory_structure(base_dir):
    """创建双眼数据的目录结构（区分双眼配对/单眼）"""
    # 定义目录：新增双眼配对目录，保留单眼目录兼容不匹配场景
    directories = [
        # 双眼配对样本目录（适配论文双眼模型）
        'train/bilateral/class_depression',
        'train/bilateral/class_non_depression',
        'val/bilateral/class_depression',
        'val/bilateral/class_non_depression',
        'test/bilateral/class_depression',
        'test/bilateral/class_non_depression',
        # 单眼样本目录（兼容左眼/右眼缺失场景）
        'train/unilateral_left/class_depression',
        'train/unilateral_left/class_non_depression',
        'train/unilateral_right/class_depression',
        'train/unilateral_right/class_non_depression',
        'val/unilateral_left/class_depression',
        'val/unilateral_left/class_non_depression',
        'val/unilateral_right/class_depression',
        'val/unilateral_right/class_non_depression',
        'test/unilateral_left/class_depression',
        'test/unilateral_left/class_non_depression',
        'test/unilateral_right/class_depression',
        'test/unilateral_right/class_non_depression'
    ]
    
    # 创建目录
    for dir_path in directories:
        full_path = os.path.join(base_dir, dir_path)
        os.makedirs(full_path, exist_ok=True)
        print(f"创建目录: {full_path}")

def get_subject_id_from_filename(filename):
    """从文件名中提取对象编号（与原逻辑一致，确保兼容性）"""
    if '__' in filename:
        return filename.split('__')[0]
    else:
        return filename.split('_')[0]

def is_depressed(row):
    """判断对象是否有抑郁症状（保持原标签逻辑）"""
    if (row['new_totdepress'] == 1 or 
        row['baseline_depression'] == '是' or 
        row['incident_depression'] == '是'):
        return True, 'class_depression'
    return False, 'class_non_depression'

def split_data(subject_ids, train_ratio=0.7, val_ratio=0.15, test_ratio=0.15):
    """将数据分割为训练集、验证集和测试集（保持原分割逻辑）"""
    if not np.isclose(train_ratio + val_ratio + test_ratio, 1.0):
        raise ValueError("训练集、验证集、测试集比例之和必须为1.0")
    
    # 分层抽样（确保各集抑郁状态分布一致，参考论文数据平衡思路）
    train_ids, temp_ids = train_test_split(
        subject_ids, test_size=1-train_ratio, random_state=42, stratify=None
    )
    val_proportion = val_ratio / (val_ratio + test_ratio)
    val_ids, test_ids = train_test_split(
        temp_ids, test_size=1-val_proportion, random_state=42, stratify=None
    )
    
    return train_ids, val_ids, test_ids

def preprocess_image(image_path, target_size=(224, 224)):
    """预处理视网膜图像（与原逻辑一致，对齐RETFound输入要求）"""
    try:
        with Image.open(image_path) as img:
            # 转换为RGB（参考论文“3通道图像输入”要求）
            if img.mode != 'RGB':
                img = img.convert('RGB')
            
            # 保持纵横比缩放+中心裁剪（避免图像变形，与论文预处理一致）
            width, height = img.size
            target_width, target_height = target_size
            ratio = min(target_width / width, target_height / height)
            new_width = int(width * ratio)
            new_height = int(height * ratio)
            
            img = img.resize((new_width, new_height), Image.LANCZOS)
            left = (new_width - target_width) // 2
            top = (new_height - target_height) // 2
            img = img.crop((left, top, left+target_width, top+target_height))
            
            return img
    except Exception as e:
        print(f"预处理图像 {image_path} 时出错: {str(e)}")
        return None

def match_bilateral_images(left_dir, right_dir):
    """
    匹配双眼图像：为每个对象找到对应的左眼和右眼图像
    返回：
    - bilateral_dict: {subject_id: {'left': [left_filename1, ...], 'right': [right_filename1, ...]}}
    - unilateral_left: {subject_id: [left_filename1, ...]}  # 仅左眼
    - unilateral_right: {subject_id: [right_filename1, ...]} # 仅右眼
    """
    # 提取左眼/右眼的对象ID-文件名映射
    left_subject_map = {}
    for filename in os.listdir(left_dir):
        if filename.endswith(('.jpg', '.jpeg', '.png')):
            subj_id = get_subject_id_from_filename(filename)
            if subj_id not in left_subject_map:
                left_subject_map[subj_id] = []
            left_subject_map[subj_id].append(filename)
    
    right_subject_map = {}
    for filename in os.listdir(right_dir):
        if filename.endswith(('.jpg', '.jpeg', '.png')):
            subj_id = get_subject_id_from_filename(filename)
            if subj_id not in right_subject_map:
                right_subject_map[subj_id] = []
            right_subject_map[subj_id].append(filename)
    
    # 分类：双眼配对、仅左眼、仅右眼
    bilateral_dict = {}
    unilateral_left = {}
    unilateral_right = {}
    
    # 先处理有双眼图像的对象
    common_subjects = set(left_subject_map.keys()) & set(right_subject_map.keys())
    for subj_id in common_subjects:
        bilateral_dict[subj_id] = {
            'left': left_subject_map[subj_id],
            'right': right_subject_map[subj_id]
        }
    
    # 处理仅左眼的对象
    left_only_subjects = set(left_subject_map.keys()) - common_subjects
    for subj_id in left_only_subjects:
        unilateral_left[subj_id] = left_subject_map[subj_id]
    
    # 处理仅右眼的对象
    right_only_subjects = set(right_subject_map.keys()) - common_subjects
    for subj_id in right_only_subjects:
        unilateral_right[subj_id] = right_subject_map[subj_id]
    
    print(f"双眼配对完成：")
    print(f"- 双眼配对对象数: {len(bilateral_dict)}")
    print(f"- 仅左眼对象数: {len(unilateral_left)}")
    print(f"- 仅右眼对象数: {len(unilateral_right)}")
    return bilateral_dict, unilateral_left, unilateral_right

def process_bilateral_images(bilateral_dict, subject_depression_map, 
                             left_dir, right_dir, output_dir, train_ids, val_ids, test_ids, target_size):
    """处理双眼配对样本（适配论文双眼模型输入）"""
    print("\n开始处理双眼配对样本...")
    processed_count = 0
    skipped_count = 0
    
    for subj_id_str, img_dict in bilateral_dict.items():
        try:
            subj_id = int(subj_id_str)
        except ValueError:
            print(f"对象ID {subj_id_str} 无效，跳过")
            skipped_count += len(img_dict['left']) + len(img_dict['right'])
            continue
        
        # 检查对象是否在抑郁状态映射中
        if subj_id not in subject_depression_map:
            print(f"对象 {subj_id} 不在Excel数据中，跳过")
            skipped_count += len(img_dict['left']) + len(img_dict['right'])
            continue
        
        # 获取抑郁状态和数据集类型
        is_depress, class_dir = subject_depression_map[subj_id]
        if subj_id in train_ids:
            dataset_dir = 'train'
        elif subj_id in val_ids:
            dataset_dir = 'val'
        else:
            dataset_dir = 'test'
        
        # 配对左眼和右眼图像（按文件名顺序配对，未匹配的单眼图像归入单眼目录）
        left_filenames = img_dict['left']
        right_filenames = img_dict['right']
        max_pair = min(len(left_filenames), len(right_filenames))
        
        # 处理可配对的图像（参考论文“4张/人”的配对逻辑）
        for i in range(max_pair):
            left_fn = left_filenames[i]
            right_fn = right_filenames[i]
            
            # 预处理双眼图像
            left_img = preprocess_image(os.path.join(left_dir, left_fn), target_size)
            right_img = preprocess_image(os.path.join(right_dir, right_fn), target_size)
            
            if left_img and right_img:
                # 保存双眼图像（文件名标注配对关系，便于后续模型读取）
                base_name = f"bilateral_{subj_id}_{i}"  # i为配对序号
                left_dest = os.path.join(output_dir, dataset_dir, 'bilateral', class_dir, f"{base_name}_left.jpg")
                right_dest = os.path.join(output_dir, dataset_dir, 'bilateral', class_dir, f"{base_name}_right.jpg")
                
                left_img.save(left_dest)
                right_img.save(right_dest)
                processed_count += 2  # 每次配对处理2张图像
                print(f"已保存双眼配对: {left_dest} | {right_dest}")
            else:
                print(f"对象 {subj_id} 的配对 {i} 预处理失败，跳过")
                skipped_count += 2
    
    print(f"双眼配对样本处理完成：共处理 {processed_count} 张图像，跳过 {skipped_count} 张图像")

def process_unilateral_images(unilateral_map, eye_type, subject_depression_map, 
                              img_dir, output_dir, train_ids, val_ids, test_ids, target_size):
    """处理单眼样本（兼容无法配对场景）"""
    print(f"\n开始处理{eye_type}单眼样本...")
    processed_count = 0
    skipped_count = 0
    unilateral_dir = f"unilateral_{eye_type}"  # 对应目录：unilateral_left/unilateral_right
    
    for subj_id_str, filenames in unilateral_map.items():
        try:
            subj_id = int(subj_id_str)
        except ValueError:
            print(f"对象ID {subj_id_str} 无效，跳过")
            skipped_count += len(filenames)
            continue
        
        if subj_id not in subject_depression_map:
            print(f"对象 {subj_id} 不在Excel数据中，跳过")
            skipped_count += len(filenames)
            continue
        
        # 获取抑郁状态和数据集类型
        is_depress, class_dir = subject_depression_map[subj_id]
        if subj_id in train_ids:
            dataset_dir = 'train'
        elif subj_id in val_ids:
            dataset_dir = 'val'
        else:
            dataset_dir = 'test'
        
        # 处理单眼图像
        for filename in filenames:
            img = preprocess_image(os.path.join(img_dir, filename), target_size)
            if img:
                dest_path = os.path.join(
                    output_dir, dataset_dir, unilateral_dir, class_dir, 
                    f"{eye_type}_{filename}"
                )
                img.save(dest_path)
                processed_count += 1
                print(f"已保存{eye_type}单眼: {dest_path}")
            else:
                print(f"{eye_type}单眼图像 {filename} 预处理失败，跳过")
                skipped_count += 1
    
    print(f"{eye_type}单眼样本处理完成：共处理 {processed_count} 张图像，跳过 {skipped_count} 张图像")

def process_bilateral_and_unilateral(left_dir, right_dir, excel_path, output_dir, target_size=(224, 224)):
    """主函数：处理双眼配对+单眼样本，适配RETFound输入"""
    # 1. 读取Excel并构建对象-抑郁状态映射
    df = pd.read_excel(excel_path)
    print(f"成功读取Excel文件，共 {len(df)} 条记录")
    
    subject_depression_map = {}
    for _, row in df.iterrows():
        subj_id = row['eid_ckd']
        if pd.notna(subj_id):
            subject_depression_map[subj_id] = is_depressed(row)
    
    # 2. 创建目录结构
    create_directory_structure(output_dir)
    
    # 3. 分割数据集（基于所有对象ID）
    all_subject_ids = list(subject_depression_map.keys())
    print(f"共发现 {len(all_subject_ids)} 个有效对象")
    train_ids, val_ids, test_ids = split_data(all_subject_ids)
    print(f"数据集分割完成 - 训练集: {len(train_ids)}, 验证集: {len(val_ids)}, 测试集: {len(test_ids)}")
    
    # 4. 匹配双眼图像
    bilateral_dict, unilateral_left, unilateral_right = match_bilateral_images(left_dir, right_dir)
    
    # 5. 处理双眼配对样本（核心，适配论文双眼模型）
    process_bilateral_images(
        bilateral_dict, subject_depression_map, left_dir, right_dir,
        output_dir, train_ids, val_ids, test_ids, target_size
    )
    
    # 6. 处理单眼样本（兼容不匹配场景）
    if unilateral_left:
        process_unilateral_images(
            unilateral_left, 'left', subject_depression_map, left_dir,
            output_dir, train_ids, val_ids, test_ids, target_size
        )
    if unilateral_right:
        process_unilateral_images(
            unilateral_right, 'right', subject_depression_map, right_dir,
            output_dir, train_ids, val_ids, test_ids, target_size
        )
    
    print("\n所有图像处理完成！")

if __name__ == "__main__":
    # 配置路径（与原代码保持一致，仅修改输出目录以区分双眼数据）
    LEFT_IMAGE_DIR = "D:/LingYi/left"          
    RIGHT_IMAGE_DIR = "D:/LingYi/right"        
    EXCEL_PATH = "D:/LingYi/0820_ukb_depression_fundus.xlsx"
    OUTPUT_DIR = "D:/LingYi/data_pre_depression_by_two_eye"  # 输出目录：双眼数据
    TARGET_SIZE = (224, 224)  # 与RETFound输入尺寸一致，参考论文224×224设置
    
    # 运行双眼+单眼处理函数
    process_bilateral_and_unilateral(LEFT_IMAGE_DIR, RIGHT_IMAGE_DIR, EXCEL_PATH, OUTPUT_DIR, TARGET_SIZE)

成功读取Excel文件，共 43445 条记录
创建目录: D:/LingYi/data_pre_depression_by_two_eye\train/bilateral/class_depression
创建目录: D:/LingYi/data_pre_depression_by_two_eye\train/bilateral/class_non_depression
创建目录: D:/LingYi/data_pre_depression_by_two_eye\val/bilateral/class_depression
创建目录: D:/LingYi/data_pre_depression_by_two_eye\val/bilateral/class_non_depression
创建目录: D:/LingYi/data_pre_depression_by_two_eye\test/bilateral/class_depression
创建目录: D:/LingYi/data_pre_depression_by_two_eye\test/bilateral/class_non_depression
创建目录: D:/LingYi/data_pre_depression_by_two_eye\train/unilateral_left/class_depression
创建目录: D:/LingYi/data_pre_depression_by_two_eye\train/unilateral_left/class_non_depression
创建目录: D:/LingYi/data_pre_depression_by_two_eye\train/unilateral_right/class_depression
创建目录: D:/LingYi/data_pre_depression_by_two_eye\train/unilateral_right/class_non_depression
创建目录: D:/LingYi/data_pre_depression_by_two_eye\val/unilateral_left/class_depression
创建目录: D:/LingYi/data_pre_depression_by_two_eye\val/u

已保存双眼配对: D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_non_depression\bilateral_1419724_0_left.jpg | D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_non_depression\bilateral_1419724_0_right.jpg
已保存双眼配对: D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_non_depression\bilateral_1417933_0_left.jpg | D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_non_depression\bilateral_1417933_0_right.jpg
已保存双眼配对: D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_non_depression\bilateral_1422772_0_left.jpg | D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_non_depression\bilateral_1422772_0_right.jpg
对象 1439510 不在Excel数据中，跳过
已保存双眼配对: D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_depression\bilateral_1068183_0_left.jpg | D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_depression\bilateral_1068183_0_right.jpg
对象 1824426 不在Excel数据中，跳过
对象 1637015 不在Excel数据中，跳过
对象 1143750 不在Excel数据中，跳过
已保存双

已保存双眼配对: D:/LingYi/data_pre_depression_by_two_eye\test\bilateral\class_non_depression\bilateral_1127019_0_left.jpg | D:/LingYi/data_pre_depression_by_two_eye\test\bilateral\class_non_depression\bilateral_1127019_0_right.jpg
对象 1140100 不在Excel数据中，跳过
已保存双眼配对: D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_non_depression\bilateral_1175233_0_left.jpg | D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_non_depression\bilateral_1175233_0_right.jpg
对象 1345025 不在Excel数据中，跳过
已保存双眼配对: D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_non_depression\bilateral_1580078_0_left.jpg | D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_non_depression\bilateral_1580078_0_right.jpg
已保存双眼配对: D:/LingYi/data_pre_depression_by_two_eye\val\bilateral\class_non_depression\bilateral_1831114_0_left.jpg | D:/LingYi/data_pre_depression_by_two_eye\val\bilateral\class_non_depression\bilateral_1831114_0_right.jpg
对象 1875071 不在Excel数据中，跳过
对象 1068730 不在Excel数据中，跳过
已保

已保存双眼配对: D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_depression\bilateral_1637686_0_left.jpg | D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_depression\bilateral_1637686_0_right.jpg
已保存双眼配对: D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_non_depression\bilateral_1860659_0_left.jpg | D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_non_depression\bilateral_1860659_0_right.jpg
已保存双眼配对: D:/LingYi/data_pre_depression_by_two_eye\val\bilateral\class_non_depression\bilateral_1526212_0_left.jpg | D:/LingYi/data_pre_depression_by_two_eye\val\bilateral\class_non_depression\bilateral_1526212_0_right.jpg
已保存双眼配对: D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_non_depression\bilateral_1638470_0_left.jpg | D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_non_depression\bilateral_1638470_0_right.jpg
对象 1802624 不在Excel数据中，跳过
已保存双眼配对: D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_non_depress

已保存双眼配对: D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_non_depression\bilateral_1277992_0_left.jpg | D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_non_depression\bilateral_1277992_0_right.jpg
已保存双眼配对: D:/LingYi/data_pre_depression_by_two_eye\val\bilateral\class_non_depression\bilateral_1644463_0_left.jpg | D:/LingYi/data_pre_depression_by_two_eye\val\bilateral\class_non_depression\bilateral_1644463_0_right.jpg
已保存双眼配对: D:/LingYi/data_pre_depression_by_two_eye\val\bilateral\class_non_depression\bilateral_1148153_0_left.jpg | D:/LingYi/data_pre_depression_by_two_eye\val\bilateral\class_non_depression\bilateral_1148153_0_right.jpg
对象 1487403 不在Excel数据中，跳过
已保存双眼配对: D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_non_depression\bilateral_1514222_0_left.jpg | D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_non_depression\bilateral_1514222_0_right.jpg
已保存双眼配对: D:/LingYi/data_pre_depression_by_two_eye\test\bilateral\class_non_depr

...

已保存双眼配对: D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_non_depression\bilateral_1760533_0_left.jpg | D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_non_depression\bilateral_1760533_0_right.jpg
对象 1799963 不在Excel数据中，跳过
已保存双眼配对: D:/LingYi/data_pre_depression_by_two_eye\val\bilateral\class_non_depression\bilateral_1598679_0_left.jpg | D:/LingYi/data_pre_depression_by_two_eye\val\bilateral\class_non_depression\bilateral_1598679_0_right.jpg
已保存双眼配对: D:/LingYi/data_pre_depression_by_two_eye\test\bilateral\class_non_depression\bilateral_1589852_0_left.jpg | D:/LingYi/data_pre_depression_by_two_eye\test\bilateral\class_non_depression\bilateral_1589852_0_right.jpg
已保存双眼配对: D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_non_depression\bilateral_1699643_0_left.jpg | D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_non_depression\bilateral_1699643_0_right.jpg
已保存双眼配对: D:/LingYi/data_pre_depression_by_two_eye\val\bilateral\class_non_dep

已保存双眼配对: D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_non_depression\bilateral_1570514_0_left.jpg | D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_non_depression\bilateral_1570514_0_right.jpg
已保存双眼配对: D:/LingYi/data_pre_depression_by_two_eye\val\bilateral\class_non_depression\bilateral_1007656_0_left.jpg | D:/LingYi/data_pre_depression_by_two_eye\val\bilateral\class_non_depression\bilateral_1007656_0_right.jpg
已保存双眼配对: D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_non_depression\bilateral_1546245_0_left.jpg | D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_non_depression\bilateral_1546245_0_right.jpg
已保存双眼配对: D:/LingYi/data_pre_depression_by_two_eye\test\bilateral\class_non_depression\bilateral_1451966_0_left.jpg | D:/LingYi/data_pre_depression_by_two_eye\test\bilateral\class_non_depression\bilateral_1451966_0_right.jpg
对象 1220725 不在Excel数据中，跳过
已保存双眼配对: D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_non_d

已保存双眼配对: D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_non_depression\bilateral_1675690_0_left.jpg | D:/LingYi/data_pre_depression_by_two_eye\train\bilateral\class_non_depression\bilateral_1675690_0_right.jpg
双眼配对样本处理完成：共处理 15720 张图像，跳过 7978 张图像

开始处理left单眼样本...
对象 1731084 不在Excel数据中，跳过
已保存left单眼: D:/LingYi/data_pre_depression_by_two_eye\train\unilateral_left\class_non_depression\left_1908363_21011_0_0.jpg
对象 1909165 不在Excel数据中，跳过
已保存left单眼: D:/LingYi/data_pre_depression_by_two_eye\train\unilateral_left\class_non_depression\left_1911321_21011_0_0.jpg
已保存left单眼: D:/LingYi/data_pre_depression_by_two_eye\val\unilateral_left\class_non_depression\left_1909423_21011_0_0.jpg
对象 1315541 不在Excel数据中，跳过
已保存left单眼: D:/LingYi/data_pre_depression_by_two_eye\train\unilateral_left\class_non_depression\left_1906960_21011_0_0.jpg
已保存left单眼: D:/LingYi/data_pre_depression_by_two_eye\train\unilateral_left\class_non_depression\left_1906698_21011_0_0.jpg
对象 1908352 不在Excel数据中，跳过
对象 1029850 不

已保存left单眼: D:/LingYi/data_pre_depression_by_two_eye\test\unilateral_left\class_depression\left_1326771_21011_0_0.jpg
对象 1909667 不在Excel数据中，跳过
已保存left单眼: D:/LingYi/data_pre_depression_by_two_eye\train\unilateral_left\class_non_depression\left_1912066_21011_0_0.jpg
已保存left单眼: D:/LingYi/data_pre_depression_by_two_eye\train\unilateral_left\class_non_depression\left_1361788_21011_0_0.jpg
已保存left单眼: D:/LingYi/data_pre_depression_by_two_eye\train\unilateral_left\class_non_depression\left_1833920_21011_0_0.jpg
已保存left单眼: D:/LingYi/data_pre_depression_by_two_eye\train\unilateral_left\class_non_depression\left_1907412_21011_0_0.jpg
已保存left单眼: D:/LingYi/data_pre_depression_by_two_eye\train\unilateral_left\class_non_depression\left_1648176_21011_0_0.jpg
对象 1908376 不在Excel数据中，跳过
对象 1086093 不在Excel数据中，跳过
已保存left单眼: D:/LingYi/data_pre_depression_by_two_eye\test\unilateral_left\class_non_depression\left_1906997_21011_0_0.jpg
对象 1762247 不在Excel数据中，跳过
已保存left单眼: D:/LingYi/data_pre_depression_by_two_eye\

已保存right单眼: D:/LingYi/data_pre_depression_by_two_eye\train\unilateral_right\class_non_depression\right_1447929_21013_0_0.jpg
已保存right单眼: D:/LingYi/data_pre_depression_by_two_eye\train\unilateral_right\class_non_depression\right_1500795_21013_0_0.jpg
已保存right单眼: D:/LingYi/data_pre_depression_by_two_eye\train\unilateral_right\class_depression\right_1211354_21013_0_0.jpg
已保存right单眼: D:/LingYi/data_pre_depression_by_two_eye\test\unilateral_right\class_non_depression\right_1444253_21013_0_0.jpg
已保存right单眼: D:/LingYi/data_pre_depression_by_two_eye\train\unilateral_right\class_non_depression\right_1226623_21013_0_0.jpg
对象 1793041 不在Excel数据中，跳过
对象 1086166 不在Excel数据中，跳过
对象 1320564 不在Excel数据中，跳过
对象 1551310 不在Excel数据中，跳过
对象 1720303 不在Excel数据中，跳过
已保存right单眼: D:/LingYi/data_pre_depression_by_two_eye\train\unilateral_right\class_non_depression\right_1038693_21013_0_0.jpg
已保存right单眼: D:/LingYi/data_pre_depression_by_two_eye\test\unilateral_right\class_non_depression\right_1505778_21013_0_0.jpg
已保存rig

In [3]:
# 选择提取双眼图片，并增强过采样少数类

import os
import pandas as pd
import shutil
import random
from sklearn.model_selection import train_test_split
from PIL import Image
import numpy as np

def create_directory_structure(base_dir):
    """创建双眼数据的目录结构（区分双眼配对/单眼）"""
    # 定义目录：新增双眼配对目录，保留单眼目录兼容不匹配场景
    directories = [
        # 双眼配对样本目录（适配论文双眼模型）
        'train/bilateral/class_depression',
        'train/bilateral/class_non_depression',
        'val/bilateral/class_depression',
        'val/bilateral/class_non_depression',
        'test/bilateral/class_depression',
        'test/bilateral/class_non_depression',
        # 单眼样本目录（兼容左眼/右眼缺失场景）
        'train/unilateral_left/class_depression',
        'train/unilateral_left/class_non_depression',
        'train/unilateral_right/class_depression',
        'train/unilateral_right/class_non_depression',
        'val/unilateral_left/class_depression',
        'val/unilateral_left/class_non_depression',
        'val/unilateral_right/class_depression',
        'val/unilateral_right/class_non_depression',
        'test/unilateral_left/class_depression',
        'test/unilateral_left/class_non_depression',
        'test/unilateral_right/class_depression',
        'test/unilateral_right/class_non_depression'
    ]
    
    # 创建目录
    for dir_path in directories:
        full_path = os.path.join(base_dir, dir_path)
        os.makedirs(full_path, exist_ok=True)
        print(f"创建目录: {full_path}")

def get_subject_id_from_filename(filename):
    """从文件名中提取对象编号（与原逻辑一致，确保兼容性）"""
    if '__' in filename:
        return filename.split('__')[0]
    else:
        return filename.split('_')[0]

def is_depressed(row):
    """判断对象是否有抑郁症状（保持原标签逻辑）"""
    if (row['new_totdepress'] == 1 or 
        row['baseline_depression'] == '是' or 
        row['incident_depression'] == '是'):
        return True, 'class_depression'
    return False, 'class_non_depression'

def split_data(subject_ids, train_ratio=0.7, val_ratio=0.15, test_ratio=0.15):
    """将数据分割为训练集、验证集和测试集（保持原分割逻辑）"""
    if not np.isclose(train_ratio + val_ratio + test_ratio, 1.0):
        raise ValueError("训练集、验证集、测试集比例之和必须为1.0")
    
    # 分层抽样（确保各集抑郁状态分布一致，参考论文数据平衡思路）
    train_ids, temp_ids = train_test_split(
        subject_ids, test_size=1-train_ratio, random_state=42, stratify=None
    )
    val_proportion = val_ratio / (val_ratio + test_ratio)
    val_ids, test_ids = train_test_split(
        temp_ids, test_size=1-val_proportion, random_state=42, stratify=None
    )
    
    return train_ids, val_ids, test_ids

def preprocess_image(image_path, target_size=(224, 224)):
    """预处理视网膜图像（与原逻辑一致，对齐RETFound输入要求）"""
    try:
        with Image.open(image_path) as img:
            # 转换为RGB（参考论文“3通道图像输入”要求）
            if img.mode != 'RGB':
                img = img.convert('RGB')
            
            # 保持纵横比缩放+中心裁剪（避免图像变形，与论文预处理一致）
            width, height = img.size
            target_width, target_height = target_size
            ratio = min(target_width / width, target_height / height)
            new_width = int(width * ratio)
            new_height = int(height * ratio)
            
            img = img.resize((new_width, new_height), Image.LANCZOS)
            left = (new_width - target_width) // 2
            top = (new_height - target_height) // 2
            img = img.crop((left, top, left+target_width, top+target_height))
            
            return img
    except Exception as e:
        print(f"预处理图像 {image_path} 时出错: {str(e)}")
        return None

def match_bilateral_images(left_dir, right_dir):
    """
    匹配双眼图像：为每个对象找到对应的左眼和右眼图像
    返回：
    - bilateral_dict: {subject_id: {'left': [left_filename1, ...], 'right': [right_filename1, ...]}}
    - unilateral_left: {subject_id: [left_filename1, ...]}  # 仅左眼
    - unilateral_right: {subject_id: [right_filename1, ...]} # 仅右眼
    """
    # 提取左眼/右眼的对象ID-文件名映射
    left_subject_map = {}
    for filename in os.listdir(left_dir):
        if filename.endswith(('.jpg', '.jpeg', '.png')):
            subj_id = get_subject_id_from_filename(filename)
            if subj_id not in left_subject_map:
                left_subject_map[subj_id] = []
            left_subject_map[subj_id].append(filename)
    
    right_subject_map = {}
    for filename in os.listdir(right_dir):
        if filename.endswith(('.jpg', '.jpeg', '.png')):
            subj_id = get_subject_id_from_filename(filename)
            if subj_id not in right_subject_map:
                right_subject_map[subj_id] = []
            right_subject_map[subj_id].append(filename)
    
    # 分类：双眼配对、仅左眼、仅右眼
    bilateral_dict = {}
    unilateral_left = {}
    unilateral_right = {}
    
    # 先处理有双眼图像的对象
    common_subjects = set(left_subject_map.keys()) & set(right_subject_map.keys())
    for subj_id in common_subjects:
        bilateral_dict[subj_id] = {
            'left': left_subject_map[subj_id],
            'right': right_subject_map[subj_id]
        }
    
    # 处理仅左眼的对象
    left_only_subjects = set(left_subject_map.keys()) - common_subjects
    for subj_id in left_only_subjects:
        unilateral_left[subj_id] = left_subject_map[subj_id]
    
    # 处理仅右眼的对象
    right_only_subjects = set(right_subject_map.keys()) - common_subjects
    for subj_id in right_only_subjects:
        unilateral_right[subj_id] = right_subject_map[subj_id]
    
    print(f"双眼配对完成：")
    print(f"- 双眼配对对象数: {len(bilateral_dict)}")
    print(f"- 仅左眼对象数: {len(unilateral_left)}")
    print(f"- 仅右眼对象数: {len(unilateral_right)}")
    return bilateral_dict, unilateral_left, unilateral_right

def process_bilateral_images(bilateral_dict, subject_depression_map, 
                             left_dir, right_dir, output_dir, train_ids, val_ids, test_ids, target_size):
    """处理双眼配对样本（适配论文双眼模型输入）"""
    print("\n开始处理双眼配对样本...")
    processed_count = 0
    skipped_count = 0
    
    for subj_id_str, img_dict in bilateral_dict.items():
        try:
            subj_id = int(subj_id_str)
        except ValueError:
            print(f"对象ID {subj_id_str} 无效，跳过")
            skipped_count += len(img_dict['left']) + len(img_dict['right'])
            continue
        
        # 检查对象是否在抑郁状态映射中
        if subj_id not in subject_depression_map:
            print(f"对象 {subj_id} 不在Excel数据中，跳过")
            skipped_count += len(img_dict['left']) + len(img_dict['right'])
            continue
        
        # 获取抑郁状态和数据集类型
        is_depress, class_dir = subject_depression_map[subj_id]
        if subj_id in train_ids:
            dataset_dir = 'train'
        elif subj_id in val_ids:
            dataset_dir = 'val'
        else:
            dataset_dir = 'test'
        
        # 配对左眼和右眼图像（按文件名顺序配对，未匹配的单眼图像归入单眼目录）
        left_filenames = img_dict['left']
        right_filenames = img_dict['right']
        max_pair = min(len(left_filenames), len(right_filenames))

        # 新增：过采样配置（仅训练集的抑郁样本执行）
        oversample_factor = 5  # 过采样倍数：将抑郁样本数量提升5倍（根据1:6.5比例调整，目标使训练集比例接近1:2）
        is_oversample = (dataset_dir == 'train') and (class_dir == 'class_depression')
        
        # 处理可配对的图像（参考论文“4张/人”的配对逻辑）
        for i in range(max_pair):
            left_fn = left_filenames[i]
            right_fn = right_filenames[i]
            
            # 预处理双眼图像
            left_img = preprocess_image(os.path.join(left_dir, left_fn), target_size)
            right_img = preprocess_image(os.path.join(right_dir, right_fn), target_size)
            
            if left_img and right_img:
                # 保存双眼图像（文件名标注配对关系，便于后续模型读取）
                base_name = f"bilateral_{subj_id}_{i}"  # i为配对序号
                left_dest = os.path.join(output_dir, dataset_dir, 'bilateral', class_dir, f"{base_name}_left.jpg")
                right_dest = os.path.join(output_dir, dataset_dir, 'bilateral', class_dir, f"{base_name}_right.jpg")
                
                left_img.save(left_dest)
                right_img.save(right_dest)
                processed_count += 2  # 每次配对处理2张图像
                
                # 2. 过采样：为抑郁训练样本生成新的合成样本
                if is_oversample:
                    for oversample_idx in range(oversample_factor):
                        # 对双眼图像执行同步增强（保留双眼关联）
                        augmented_left = augment_image(left_img)  # 自定义增强函数
                        augmented_right = augment_image(right_img)  # 左右眼执行相同增强

                        # 保存增强后的配对样本（标注oversample标识）
                        aug_base_name = f"bilateral_{subj_id}_{i}_aug{oversample_idx}"
                        aug_left_dest = os.path.join(output_dir, dataset_dir, 'bilateral', class_dir, f"{aug_base_name}_left.jpg")
                        aug_right_dest = os.path.join(output_dir, dataset_dir, 'bilateral', class_dir, f"{aug_base_name}_right.jpg")
                        augmented_left.save(aug_left_dest)
                        augmented_right.save(aug_right_dest)
                        processed_count += 2
                        print(f"已保存过采样双眼配对: {aug_left_dest} | {aug_right_dest}")                
            else:
                print(f"对象 {subj_id} 的配对 {i} 预处理失败，跳过")
                skipped_count += 2
    
    print(f"双眼配对样本处理完成：共处理 {processed_count} 张图像，跳过 {skipped_count} 张图像")

# 新增：图像增强函数（同步作用于左右眼）
def augment_image(img):
    """对单张图像执行增强，用于过采样生成新样本"""
    from torchvision import transforms
    import random
    
    # 定义增强组合（确保变换合理，不破坏眼底特征）
    augment_transform = transforms.Compose([
#         transforms.RandomHorizontalFlip(p=0.5),  # 水平翻转（双眼同步，合理）
        transforms.RandomRotation(degrees=(-3, 3)),  # 小角度旋转
        transforms.ColorJitter(brightness=0.1, contrast=0.1),  # 亮度/对比度微调
    ])
    
    # 转换为PIL图像执行增强（若已为PIL格式可直接处理）
    if not isinstance(img, Image.Image):
        img = Image.fromarray(np.uint8(img))
    return augment_transform(img)    
    
def process_unilateral_images(unilateral_map, eye_type, subject_depression_map, 
                              img_dir, output_dir, train_ids, val_ids, test_ids, target_size):
    """处理单眼样本（兼容无法配对场景）"""
    print(f"\n开始处理{eye_type}单眼样本...")
    processed_count = 0
    skipped_count = 0
    unilateral_dir = f"unilateral_{eye_type}"  # 对应目录：unilateral_left/unilateral_right
    
    for subj_id_str, filenames in unilateral_map.items():
        try:
            subj_id = int(subj_id_str)
        except ValueError:
            print(f"对象ID {subj_id_str} 无效，跳过")
            skipped_count += len(filenames)
            continue
        
        if subj_id not in subject_depression_map:
            print(f"对象 {subj_id} 不在Excel数据中，跳过")
            skipped_count += len(filenames)
            continue
        
        # 获取抑郁状态和数据集类型
        is_depress, class_dir = subject_depression_map[subj_id]
        if subj_id in train_ids:
            dataset_dir = 'train'
        elif subj_id in val_ids:
            dataset_dir = 'val'
        else:
            dataset_dir = 'test'
        
        # 处理单眼图像
        for filename in filenames:
            img = preprocess_image(os.path.join(img_dir, filename), target_size)
            if img:
                dest_path = os.path.join(
                    output_dir, dataset_dir, unilateral_dir, class_dir, 
                    f"{eye_type}_{filename}"
                )
                img.save(dest_path)
                processed_count += 1
                print(f"已保存{eye_type}单眼: {dest_path}")
            else:
                print(f"{eye_type}单眼图像 {filename} 预处理失败，跳过")
                skipped_count += 1
    
    print(f"{eye_type}单眼样本处理完成：共处理 {processed_count} 张图像，跳过 {skipped_count} 张图像")

def process_bilateral_and_unilateral(left_dir, right_dir, excel_path, output_dir, target_size=(224, 224)):
    """主函数：处理双眼配对+单眼样本，适配RETFound输入"""
    # 1. 读取Excel并构建对象-抑郁状态映射
    df = pd.read_excel(excel_path)
    print(f"成功读取Excel文件，共 {len(df)} 条记录")
    
    subject_depression_map = {}
    for _, row in df.iterrows():
        subj_id = row['eid_ckd']
        if pd.notna(subj_id):
            subject_depression_map[subj_id] = is_depressed(row)
    
    # 2. 创建目录结构
    create_directory_structure(output_dir)
    
    # 3. 分割数据集（基于所有对象ID）
    all_subject_ids = list(subject_depression_map.keys())
    print(f"共发现 {len(all_subject_ids)} 个有效对象")
    train_ids, val_ids, test_ids = split_data(all_subject_ids)
    print(f"数据集分割完成 - 训练集: {len(train_ids)}, 验证集: {len(val_ids)}, 测试集: {len(test_ids)}")
    
    # 4. 匹配双眼图像
    bilateral_dict, unilateral_left, unilateral_right = match_bilateral_images(left_dir, right_dir)
    
    # 5. 处理双眼配对样本（核心，适配论文双眼模型）
    process_bilateral_images(
        bilateral_dict, subject_depression_map, left_dir, right_dir,
        output_dir, train_ids, val_ids, test_ids, target_size
    )
    
    # 6. 处理单眼样本（兼容不匹配场景）
    if unilateral_left:
        process_unilateral_images(
            unilateral_left, 'left', subject_depression_map, left_dir,
            output_dir, train_ids, val_ids, test_ids, target_size
        )
    if unilateral_right:
        process_unilateral_images(
            unilateral_right, 'right', subject_depression_map, right_dir,
            output_dir, train_ids, val_ids, test_ids, target_size
        )
    
    print("\n所有图像处理完成！")

if __name__ == "__main__":
    # 配置路径（与原代码保持一致，仅修改输出目录以区分双眼数据）
    LEFT_IMAGE_DIR = "D:/LingYi/left"          
    RIGHT_IMAGE_DIR = "D:/LingYi/right"        
    EXCEL_PATH = "D:/LingYi/0820_ukb_depression_fundus.xlsx"
    OUTPUT_DIR = "D:/LingYi/data_pre_depression_by_two_eye_enhance"  # 输出目录：双眼数据
    TARGET_SIZE = (224, 224)  # 与RETFound输入尺寸一致，参考论文224×224设置
    
    # 运行双眼+单眼处理函数
    process_bilateral_and_unilateral(LEFT_IMAGE_DIR, RIGHT_IMAGE_DIR, EXCEL_PATH, OUTPUT_DIR, TARGET_SIZE)

成功读取Excel文件，共 43445 条记录
创建目录: D:/LingYi/data_pre_depression_by_two_eye_enhance\train/bilateral/class_depression
创建目录: D:/LingYi/data_pre_depression_by_two_eye_enhance\train/bilateral/class_non_depression
创建目录: D:/LingYi/data_pre_depression_by_two_eye_enhance\val/bilateral/class_depression
创建目录: D:/LingYi/data_pre_depression_by_two_eye_enhance\val/bilateral/class_non_depression
创建目录: D:/LingYi/data_pre_depression_by_two_eye_enhance\test/bilateral/class_depression
创建目录: D:/LingYi/data_pre_depression_by_two_eye_enhance\test/bilateral/class_non_depression
创建目录: D:/LingYi/data_pre_depression_by_two_eye_enhance\train/unilateral_left/class_depression
创建目录: D:/LingYi/data_pre_depression_by_two_eye_enhance\train/unilateral_left/class_non_depression
创建目录: D:/LingYi/data_pre_depression_by_two_eye_enhance\train/unilateral_right/class_depression
创建目录: D:/LingYi/data_pre_depression_by_two_eye_enhance\train/unilateral_right/class_non_depression
创建目录: D:/LingYi/data_pre_depression_by_two_eye_enhance\v

对象 1575128 不在Excel数据中，跳过
对象 1773522 不在Excel数据中，跳过
已保存过采样双眼配对: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1385975_0_aug0_left.jpg | D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1385975_0_aug0_right.jpg
已保存过采样双眼配对: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1385975_0_aug1_left.jpg | D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1385975_0_aug1_right.jpg
已保存过采样双眼配对: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1385975_0_aug2_left.jpg | D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1385975_0_aug2_right.jpg
已保存过采样双眼配对: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1385975_0_aug3_left.jpg | D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depressi

已保存过采样双眼配对: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1037907_0_aug0_left.jpg | D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1037907_0_aug0_right.jpg
已保存过采样双眼配对: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1037907_0_aug1_left.jpg | D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1037907_0_aug1_right.jpg
已保存过采样双眼配对: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1037907_0_aug2_left.jpg | D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1037907_0_aug2_right.jpg
已保存过采样双眼配对: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1037907_0_aug3_left.jpg | D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1037907_0_aug3_right.jpg
已保存过采样双眼配对: 

对象 1799064 不在Excel数据中，跳过
对象 1065425 不在Excel数据中，跳过
对象 1515738 不在Excel数据中，跳过
对象 1506906 不在Excel数据中，跳过
对象 1617091 不在Excel数据中，跳过
对象 1418764 不在Excel数据中，跳过
对象 1675634 不在Excel数据中，跳过
对象 1487563 不在Excel数据中，跳过
对象 1011170 不在Excel数据中，跳过
对象 1713423 不在Excel数据中，跳过
对象 1887118 不在Excel数据中，跳过
对象 1218617 不在Excel数据中，跳过
对象 1704922 不在Excel数据中，跳过
对象 1526428 不在Excel数据中，跳过
对象 1433671 不在Excel数据中，跳过
对象 1901964 不在Excel数据中，跳过
对象 1816774 不在Excel数据中，跳过
已保存过采样双眼配对: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1629857_0_aug0_left.jpg | D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1629857_0_aug0_right.jpg
已保存过采样双眼配对: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1629857_0_aug1_left.jpg | D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1629857_0_aug1_right.jpg
已保存过采样双眼配对: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\clas

对象 1333915 不在Excel数据中，跳过
对象 1173418 不在Excel数据中，跳过
对象 1733047 不在Excel数据中，跳过
对象 1571512 不在Excel数据中，跳过
对象 1512415 不在Excel数据中，跳过
对象 1677154 不在Excel数据中，跳过
对象 1439796 不在Excel数据中，跳过
对象 1146255 不在Excel数据中，跳过
对象 1257493 不在Excel数据中，跳过
对象 1226103 不在Excel数据中，跳过
已保存过采样双眼配对: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1503237_0_aug0_left.jpg | D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1503237_0_aug0_right.jpg
已保存过采样双眼配对: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1503237_0_aug1_left.jpg | D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1503237_0_aug1_right.jpg
已保存过采样双眼配对: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1503237_0_aug2_left.jpg | D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1503237_0_aug2_right.jpg
已保存过采样双眼配

...

已保存过采样双眼配对: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1024584_0_aug0_left.jpg | D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1024584_0_aug0_right.jpg
已保存过采样双眼配对: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1024584_0_aug1_left.jpg | D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1024584_0_aug1_right.jpg
已保存过采样双眼配对: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1024584_0_aug2_left.jpg | D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1024584_0_aug2_right.jpg
已保存过采样双眼配对: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1024584_0_aug3_left.jpg | D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1024584_0_aug3_right.jpg
已保存过采样双眼配对: 

对象 1327494 不在Excel数据中，跳过
对象 1565318 不在Excel数据中，跳过
对象 1852858 不在Excel数据中，跳过
对象 1162034 不在Excel数据中，跳过
对象 1393878 不在Excel数据中，跳过
对象 1432674 不在Excel数据中，跳过
对象 1723552 不在Excel数据中，跳过
对象 1330971 不在Excel数据中，跳过
已保存过采样双眼配对: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1464152_0_aug0_left.jpg | D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1464152_0_aug0_right.jpg
已保存过采样双眼配对: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1464152_0_aug1_left.jpg | D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1464152_0_aug1_right.jpg
已保存过采样双眼配对: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1464152_0_aug2_left.jpg | D:/LingYi/data_pre_depression_by_two_eye_enhance\train\bilateral\class_depression\bilateral_1464152_0_aug2_right.jpg
已保存过采样双眼配对: D:/LingYi/data_pre_depression_by_two_eye_enhanc

已保存left单眼: D:/LingYi/data_pre_depression_by_two_eye_enhance\val\unilateral_left\class_non_depression\left_1908961_21011_0_0.jpg
已保存left单眼: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\unilateral_left\class_non_depression\left_1908363_21011_0_0.jpg
已保存left单眼: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\unilateral_left\class_non_depression\left_1912138_21011_0_0.jpg
对象 1909834 不在Excel数据中，跳过
已保存left单眼: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\unilateral_left\class_non_depression\left_1911676_21011_0_0.jpg
对象 1906853 不在Excel数据中，跳过
对象 1906862 不在Excel数据中，跳过
已保存left单眼: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\unilateral_left\class_depression\left_1909927_21011_0_0.jpg
对象 1241882 不在Excel数据中，跳过
对象 1908101 不在Excel数据中，跳过
对象 1908974 不在Excel数据中，跳过
已保存left单眼: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\unilateral_left\class_non_depression\left_1910276_21011_0_0.jpg
已保存left单眼: D:/LingYi/data_pre_depression_by_two_eye_enhance\test\unilateral_

已保存left单眼: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\unilateral_left\class_non_depression\left_1022537_21011_0_0.jpg
对象 1752257 不在Excel数据中，跳过
已保存left单眼: D:/LingYi/data_pre_depression_by_two_eye_enhance\test\unilateral_left\class_non_depression\left_1904976_21011_0_0.jpg
已保存left单眼: D:/LingYi/data_pre_depression_by_two_eye_enhance\val\unilateral_left\class_non_depression\left_1909398_21011_0_0.jpg
对象 1462424 不在Excel数据中，跳过
对象 1059810 不在Excel数据中，跳过
对象 1715500 不在Excel数据中，跳过
已保存left单眼: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\unilateral_left\class_non_depression\left_1906698_21011_0_0.jpg
已保存left单眼: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\unilateral_left\class_non_depression\left_1910774_21011_0_0.jpg
已保存left单眼: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\unilateral_left\class_non_depression\left_1169478_21011_0_0.jpg
对象 1735055 不在Excel数据中，跳过
对象 1315541 不在Excel数据中，跳过
对象 1471871 不在Excel数据中，跳过
已保存left单眼: D:/LingYi/data_pre_depression_by_two_

已保存right单眼: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\unilateral_right\class_non_depression\right_1108468_21013_0_0.jpg
对象 1693702 不在Excel数据中，跳过
对象 1394071 不在Excel数据中，跳过
已保存right单眼: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\unilateral_right\class_depression\right_1114423_21013_0_0.jpg
对象 1415885 不在Excel数据中，跳过
已保存right单眼: D:/LingYi/data_pre_depression_by_two_eye_enhance\val\unilateral_right\class_non_depression\right_1734038_21013_0_0.jpg
对象 1166114 不在Excel数据中，跳过
已保存right单眼: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\unilateral_right\class_non_depression\right_1500795_21013_0_0.jpg
对象 1134621 不在Excel数据中，跳过
已保存right单眼: D:/LingYi/data_pre_depression_by_two_eye_enhance\val\unilateral_right\class_non_depression\right_1272445_21013_0_0.jpg
对象 1164405 不在Excel数据中，跳过
已保存right单眼: D:/LingYi/data_pre_depression_by_two_eye_enhance\train\unilateral_right\class_non_depression\right_1473241_21013_0_0.jpg
已保存right单眼: D:/LingYi/data_pre_depression_by_two_eye_enhance

In [17]:
# 读取统计表格并提取相关结构化特征并保存（支持按ID匹配）
import os
import pandas as pd
import torch
import joblib
from sklearn.preprocessing import OneHotEncoder, StandardScaler
from sklearn.compose import ColumnTransformer

# ---------------------------
# 一、提取眼图样本ID及划分信息
# ---------------------------
# 1. 定义路径
eye_data_root = "D:/LingYi/data_pre_depression_by_right_eye"  # 眼图根目录
subsets = ["train", "val", "test"]
classes = ["class_depression", "class_non_depression"]

# 2. 提取各子集的样本ID（按图像文件名解析，保留ID列表而非仅集合）
# 关键修改：用列表存储ID，确保后续与结构化特征的ID顺序完全对齐
subset_id_list = {subset: [] for subset in subsets}  # 存储ID列表（保留顺序）
subset_id_set = {subset: set() for subset in subsets}  # 存储ID集合（用于去重）

for subset in subsets:
    for cls in classes:
        img_dir = os.path.join(eye_data_root, subset, cls)
        if not os.path.exists(img_dir):
            continue
        # 遍历所有.jpg图像
        for img_name in os.listdir(img_dir):
            if img_name.endswith(".jpg"):
                # 提取样本ID（按实际文件名格式：第2个"_"分割，如"right_2545707_xxx.jpg"→"2545707"）
                sample_id = img_name.split("_")[1]
                # 去重：避免同一ID的重复图像（如多张眼图对应同一患者）
                if sample_id not in subset_id_set[subset]:
                    subset_id_set[subset].add(sample_id)
                    subset_id_list[subset].append(sample_id)  # 加入列表，保留顺序

# 3. 转换为DataFrame（ID列与表格数据的eid_ckd匹配）
id_mapping = []
for subset in subsets:
    # 关键：按ID列表顺序生成映射，确保后续结构化特征顺序与ID列表一致
    for sample_id in subset_id_list[subset]:
        id_mapping.append({"eid_ckd": sample_id, "subset": subset})
id_mapping_df = pd.DataFrame(id_mapping)

print(f"图像划分结果：train={len(subset_id_list['train'])} | val={len(subset_id_list['val'])} | test={len(subset_id_list['test'])}")


# ---------------------------
# 二、按眼图ID提取并匹配结构化数据（核心：确保结构化特征顺序与眼图ID列表一致）
# ---------------------------
# 1. 加载原始表格数据
df_original = pd.read_excel("D:/LingYi/0820_ukb_depression_fundus.xlsx")

# 2. 定义目标结构化特征
target_features = [
    "gender", "baselineage", "smokingc", "drinkc", "bmi",
    "townsend", "edu", "hbp", "dmstatus", "hyperlipidemia"
]

# 3. 筛选特征并保留eid_ckd（样本ID），转换为字符串避免类型不匹配
df_struct_with_id = df_original[["eid_ckd"] + target_features].copy()
df_struct_with_id["eid_ckd"] = df_struct_with_id["eid_ckd"].astype(str)
id_mapping_df["eid_ckd"] = id_mapping_df["eid_ckd"].astype(str)

# 4. 关联划分信息（通过eid_ckd匹配，仅保留眼图存在的样本）
df_struct_labeled = pd.merge(
    id_mapping_df,  # 左表：眼图ID列表（按顺序）
    df_struct_with_id,  # 右表：结构化数据
    on="eid_ckd", 
    how="left"  # 关键：按眼图ID列表顺序保留，确保后续特征顺序与眼图一致
)

# 5. 按subset拆分train/val/test（严格遵循眼图ID列表顺序）
# 关键：用isin(subset_id_list[subset])而非按subset列筛选，确保顺序完全对齐
df_train = df_struct_labeled[df_struct_labeled["eid_ckd"].isin(subset_id_list["train"])].drop(columns=["subset"])
df_val = df_struct_labeled[df_struct_labeled["eid_ckd"].isin(subset_id_list["val"])].drop(columns=["subset"])
df_test = df_struct_labeled[df_struct_labeled["eid_ckd"].isin(subset_id_list["test"])].drop(columns=["subset"])

# 进一步确保顺序与眼图ID列表完全一致
df_train = df_train.set_index("eid_ckd").loc[subset_id_list["train"]].reset_index()
df_val = df_val.set_index("eid_ckd").loc[subset_id_list["val"]].reset_index()
df_test = df_test.set_index("eid_ckd").loc[subset_id_list["test"]].reset_index()

print(f"结构化特征划分：train={len(df_train)} | val={len(df_val)} | test={len(df_test)}")
# 验证：结构化数据的ID顺序与眼图ID列表是否一致（必须通过）
assert df_train["eid_ckd"].tolist() == subset_id_list["train"], "Train集ID顺序不匹配！"
assert df_val["eid_ckd"].tolist() == subset_id_list["val"], "Val集ID顺序不匹配！"
assert df_test["eid_ckd"].tolist() == subset_id_list["test"], "Test集ID顺序不匹配！"


# ---------------------------
# 三、结构化数据缺失值补齐
# ---------------------------
# 1. 连续变量补齐（用train的中位数）
for col in ["baselineage", "bmi", "townsend"]:
    fill_value = df_train[col].median()
    df_train[col] = df_train[col].fillna(fill_value)
    df_val[col] = df_val[col].fillna(fill_value)
    df_test[col] = df_test[col].fillna(fill_value)

# 2. 分类变量补齐
gender_mode = df_train["gender"].mode()[0]
df_train["gender"] = df_train["gender"].fillna(gender_mode)
df_val["gender"] = df_val["gender"].fillna(gender_mode)
df_test["gender"] = df_test["gender"].fillna(gender_mode)

for col in ["smokingc", "drinkc"]:
    train_mode = df_train[col].mode()[0]
    df_train[col] = df_train[col].fillna(train_mode)
    df_val[col] = df_val[col].fillna("unknown")
    df_test[col] = df_test[col].fillna("unknown")

# 3. 二元变量补齐
for col in ["hbp", "dmstatus", "hyperlipidemia"]:
    train_mode = df_train[col].mode()[0]
    df_train[col] = df_train[col].fillna(train_mode)
    df_val[col] = df_val[col].fillna(train_mode)
    df_test[col] = df_test[col].fillna(train_mode)


# ---------------------------
# 四、特征预处理（保留ID列表）
# ---------------------------
# 1. 定义特征类型
categorical_cols = ["gender", "smokingc", "drinkc", "edu"]
continuous_cols = ["baselineage", "bmi", "townsend", "hbp", "dmstatus", "hyperlipidemia"]

# 2. 定义预处理管道
preprocessor = ColumnTransformer(
    transformers=[
        ("cat", OneHotEncoder(sparse_output=False, handle_unknown="ignore"), categorical_cols),
        ("num", StandardScaler(), continuous_cols)
    ])

# 3. 拟合并转换特征（保留ID列，仅对特征列预处理）
# 提取特征列（排除eid_ckd）
train_feats = df_train.drop(columns=["eid_ckd"])
val_feats = df_val.drop(columns=["eid_ckd"])
test_feats = df_test.drop(columns=["eid_ckd"])

# 预处理
struct_feat_train = preprocessor.fit_transform(train_feats)
struct_feat_val = preprocessor.transform(val_feats)
struct_feat_test = preprocessor.transform(test_feats)

# 转换为Tensor
struct_feat_train = torch.tensor(struct_feat_train, dtype=torch.float32)
struct_feat_val = torch.tensor(struct_feat_val, dtype=torch.float32)
struct_feat_test = torch.tensor(struct_feat_test, dtype=torch.float32)


# ---------------------------
# 五、保存数据（保存ID列表，支持后续按ID匹配）
# ---------------------------
# 1. 定义保存路径
struct_feat_dir = os.path.join(eye_data_root, "structured_features")
os.makedirs(struct_feat_dir, exist_ok=True)
print(f"结构化特征将保存到：{struct_feat_dir}")

# 2. 保存预处理后的结构化特征（Tensor格式）
torch.save(struct_feat_train, os.path.join(struct_feat_dir, "train_struct_feats.pt"))
torch.save(struct_feat_val, os.path.join(struct_feat_dir, "val_struct_feats.pt"))
torch.save(struct_feat_test, os.path.join(struct_feat_dir, "test_struct_feats.pt"))

# 3. 保存各子集的ID列表（用于后续按ID匹配）
# 保存为CSV，方便查看和加载
pd.DataFrame({"eid_ckd": subset_id_list["train"]}).to_csv(
    os.path.join(struct_feat_dir, "train_struct_ids.csv"), index=False
)
pd.DataFrame({"eid_ckd": subset_id_list["val"]}).to_csv(
    os.path.join(struct_feat_dir, "val_struct_ids.csv"), index=False
)
pd.DataFrame({"eid_ckd": subset_id_list["test"]}).to_csv(
    os.path.join(struct_feat_dir, "test_struct_ids.csv"), index=False
)

# 4. 保存预处理管道
joblib.dump(preprocessor, os.path.join(struct_feat_dir, "struct_preprocessor.pkl"))

print("=== 保存完成 ===")
print("1. 结构化特征：train_struct_feats.pt / val_struct_feats.pt / test_struct_feats.pt")
print("2. ID列表（用于按ID匹配）：train_struct_ids.csv / val_struct_ids.csv / test_struct_ids.csv")
print("3. 预处理管道：struct_preprocessor.pkl")

图像划分结果：train=2528 | val=1212 | test=1185
结构化特征划分：train=2528 | val=1212 | test=1185
结构化特征将保存到：D:/LingYi/data_pre_depression_by_right_eye\structured_features
=== 保存完成 ===
1. 结构化特征：train_struct_feats.pt / val_struct_feats.pt / test_struct_feats.pt
2. ID列表（用于按ID匹配）：train_struct_ids.csv / val_struct_ids.csv / test_struct_ids.csv
3. 预处理管道：struct_preprocessor.pkl
